# Baseline Automatic Speech Recognition with Transformer
https://keras.io/examples/audio/transformer_asr/

**Author:** [Apoorv Nandan](https://twitter.com/NandanApoorv)<br>
**Date created:** 2021/01/13<br>
**Last modified:** 2021/01/13<br>
**Description:** Training a sequence-to-sequence Transformer for automatic speech recognition.

## Introduction

Automatic speech recognition (ASR) consists of transcribing audio speech segments into text.
ASR can be treated as a sequence-to-sequence problem, where the
audio can be represented as a sequence of feature vectors
and the text as a sequence of characters, words, or subword tokens.

For this demonstration, we will use the LJSpeech dataset from the
[LibriVox](https://librivox.org/) project. It consists of short
audio clips of a single speaker reading passages from 7 non-fiction books.
Our model will be similar to the original Transformer (both encoder and decoder)
as proposed in the paper, "Attention is All You Need".


**References:**

- [Attention is All You Need](https://papers.nips.cc/paper/2017/file/3f5ee243547dee91fbd053c1c4a845aa-Paper.pdf)
- [Very Deep Self-Attention Networks for End-to-End Speech Recognition](https://arxiv.org/pdf/1904.13377.pdf)
- [Speech Transformers](https://ieeexplore.ieee.org/document/8462506)
- [LJSpeech Dataset](https://keithito.com/LJ-Speech-Dataset/)

In [ ]:

import os
import random
from glob import glob
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers


## Define the Transformer Input Layer

When processing past target tokens for the decoder, we compute the sum of
position embeddings and token embeddings.

When processing audio features, we apply convolutional layers to downsample
them (via convolution stides) and process local relationships.

In [ ]:

class TokenEmbedding(layers.Layer):
    def __init__(self, num_vocab=1000, maxlen=100, num_hid=64):
        super().__init__()
        self.emb = tf.keras.layers.Embedding(num_vocab, num_hid)
        self.pos_emb = layers.Embedding(input_dim=maxlen, output_dim=num_hid)

    def call(self, x):
        maxlen = tf.shape(x)[-1]
        x = self.emb(x)
        positions = tf.range(start=0, limit=maxlen, delta=1)
        positions = self.pos_emb(positions)
        return x + positions


class SpeechFeatureEmbedding(layers.Layer):
    def __init__(self, num_hid=64, maxlen=100):
        super().__init__()
        self.conv1 = tf.keras.layers.Conv1D(
            num_hid, 11, strides=2, padding="same", activation="relu"
        )
        self.conv2 = tf.keras.layers.Conv1D(
            num_hid, 11, strides=2, padding="same", activation="relu"
        )
        self.conv3 = tf.keras.layers.Conv1D(
            num_hid, 11, strides=2, padding="same", activation="relu"
        )
        self.pos_emb = layers.Embedding(input_dim=maxlen, output_dim=num_hid)

    def call(self, x):
        x = self.conv1(x)
        x = self.conv2(x)
        return self.conv3(x)


## Transformer Encoder Layer

In [ ]:

class TransformerEncoder(layers.Layer):
    def __init__(self, embed_dim, num_heads, feed_forward_dim, rate=0.1):
        super().__init__()
        self.att = layers.MultiHeadAttention(num_heads=num_heads, key_dim=embed_dim)
        self.ffn = keras.Sequential(
            [
                layers.Dense(feed_forward_dim, activation="relu"),
                layers.Dense(embed_dim),
            ]
        )
        self.layernorm1 = layers.LayerNormalization(epsilon=1e-6)
        self.layernorm2 = layers.LayerNormalization(epsilon=1e-6)
        self.dropout1 = layers.Dropout(rate)
        self.dropout2 = layers.Dropout(rate)

    def call(self, inputs, training):
        attn_output = self.att(inputs, inputs)
        attn_output = self.dropout1(attn_output, training=training)
        out1 = self.layernorm1(inputs + attn_output)
        ffn_output = self.ffn(out1)
        ffn_output = self.dropout2(ffn_output, training=training)
        return self.layernorm2(out1 + ffn_output)


## Transformer Decoder Layer

In [ ]:

class TransformerDecoder(layers.Layer):
    def __init__(self, embed_dim, num_heads, feed_forward_dim, dropout_rate=0.1):
        super().__init__()
        self.layernorm1 = layers.LayerNormalization(epsilon=1e-6)
        self.layernorm2 = layers.LayerNormalization(epsilon=1e-6)
        self.layernorm3 = layers.LayerNormalization(epsilon=1e-6)
        self.self_att = layers.MultiHeadAttention(
            num_heads=num_heads, key_dim=embed_dim
        )
        self.enc_att = layers.MultiHeadAttention(num_heads=num_heads, key_dim=embed_dim)
        self.self_dropout = layers.Dropout(0.5)
        self.enc_dropout = layers.Dropout(0.1)
        self.ffn_dropout = layers.Dropout(0.1)
        self.ffn = keras.Sequential(
            [
                layers.Dense(feed_forward_dim, activation="relu"),
                layers.Dense(embed_dim),
            ]
        )

    def causal_attention_mask(self, batch_size, n_dest, n_src, dtype):
        """Masks the upper half of the dot product matrix in self attention.

        This prevents flow of information from future tokens to current token.
        1's in the lower triangle, counting from the lower right corner.
        """
        i = tf.range(n_dest)[:, None]
        j = tf.range(n_src)
        m = i >= j - n_src + n_dest
        mask = tf.cast(m, dtype)
        mask = tf.reshape(mask, [1, n_dest, n_src])
        mult = tf.concat(
            [tf.expand_dims(batch_size, -1), tf.constant([1, 1], dtype=tf.int32)], 0
        )
        return tf.tile(mask, mult)

    def call(self, enc_out, target):
        input_shape = tf.shape(target)
        batch_size = input_shape[0]
        seq_len = input_shape[1]
        causal_mask = self.causal_attention_mask(batch_size, seq_len, seq_len, tf.bool)
        target_att = self.self_att(target, target, attention_mask=causal_mask)
        target_norm = self.layernorm1(target + self.self_dropout(target_att))
        enc_out = self.enc_att(target_norm, enc_out)
        enc_out_norm = self.layernorm2(self.enc_dropout(enc_out) + target_norm)
        ffn_out = self.ffn(enc_out_norm)
        ffn_out_norm = self.layernorm3(enc_out_norm + self.ffn_dropout(ffn_out))
        return ffn_out_norm


## Complete the Transformer model

Our model takes audio spectrograms as inputs and predicts a sequence of characters.
During training, we give the decoder the target character sequence shifted to the left
as input. During inference, the decoder uses its own past predictions to predict the
next token.

In [ ]:

class Transformer(keras.Model):
    def __init__(
        self,
        num_hid=64,
        num_head=2,
        num_feed_forward=128,
        source_maxlen=100,
        target_maxlen=100,
        num_layers_enc=4,
        num_layers_dec=1,
        num_classes=10,
    ):
        super().__init__()
        self.loss_metric = keras.metrics.Mean(name="loss")
        self.num_layers_enc = num_layers_enc
        self.num_layers_dec = num_layers_dec
        self.target_maxlen = target_maxlen
        self.num_classes = num_classes

        self.enc_input = SpeechFeatureEmbedding(num_hid=num_hid, maxlen=source_maxlen)
        self.dec_input = TokenEmbedding(
            num_vocab=num_classes, maxlen=target_maxlen, num_hid=num_hid
        )

        self.encoder = keras.Sequential(
            [self.enc_input]
            + [
                TransformerEncoder(num_hid, num_head, num_feed_forward)
                for _ in range(num_layers_enc)
            ]
        )

        for i in range(num_layers_dec):
            setattr(
                self,
                f"dec_layer_{i}",
                TransformerDecoder(num_hid, num_head, num_feed_forward),
            )

        self.classifier = layers.Dense(num_classes)

    def decode(self, enc_out, target):
        y = self.dec_input(target)
        for i in range(self.num_layers_dec):
            y = getattr(self, f"dec_layer_{i}")(enc_out, y)
        return y

    def call(self, inputs):
        source = inputs[0]
        target = inputs[1]
        x = self.encoder(source)
        y = self.decode(x, target)
        return self.classifier(y)

    @property
    def metrics(self):
        return [self.loss_metric]

    def train_step(self, batch):
        """Processes one batch inside model.fit()."""
        source = batch["source"]
        target = batch["target"]
        dec_input = target[:, :-1]
        dec_target = target[:, 1:]
        with tf.GradientTape() as tape:
            preds = self([source, dec_input])
            one_hot = tf.one_hot(dec_target, depth=self.num_classes)
            mask = tf.math.logical_not(tf.math.equal(dec_target, 0))
            loss = self.compiled_loss(one_hot, preds, sample_weight=mask)
        trainable_vars = self.trainable_variables
        gradients = tape.gradient(loss, trainable_vars)
        self.optimizer.apply_gradients(zip(gradients, trainable_vars))
        self.loss_metric.update_state(loss)
        return {"loss": self.loss_metric.result()}

    def test_step(self, batch):
        source = batch["source"]
        target = batch["target"]
        dec_input = target[:, :-1]
        dec_target = target[:, 1:]
        preds = self([source, dec_input])
        one_hot = tf.one_hot(dec_target, depth=self.num_classes)
        mask = tf.math.logical_not(tf.math.equal(dec_target, 0))
        loss = self.compiled_loss(one_hot, preds, sample_weight=mask)
        self.loss_metric.update_state(loss)
        return {"loss": self.loss_metric.result()}

    def generate(self, source, target_start_token_idx):
        """Performs inference over one batch of inputs using greedy decoding."""
        bs = tf.shape(source)[0]
        enc = self.encoder(source)
        dec_input = tf.ones((bs, 1), dtype=tf.int32) * target_start_token_idx
        dec_logits = []
        for i in range(self.target_maxlen - 1):
            dec_out = self.decode(enc, dec_input)
            logits = self.classifier(dec_out)
            logits = tf.argmax(logits, axis=-1, output_type=tf.int32)
            last_logit = tf.expand_dims(logits[:, -1], axis=-1)
            dec_logits.append(last_logit)
            dec_input = tf.concat([dec_input, last_logit], axis=-1)
        return dec_input


## Download the dataset

Note: This requires ~3.6 GB of disk space and
takes ~5 minutes for the extraction of files.

In [ ]:
keras.utils.get_file(
    os.path.join(os.getcwd(), "data.tar.gz"),
    "https://data.keithito.com/data/speech/LJSpeech-1.1.tar.bz2",
    extract=True,
    archive_format="tar",
    cache_dir=".",
)


saveto = "./datasets/LJSpeech-1.1"
wavs = glob("{}/**/*.wav".format(saveto), recursive=True)

id_to_text = {}
with open(os.path.join(saveto, "metadata.csv"), encoding="utf-8") as f:
    for line in f:
        id = line.strip().split("|")[0]
        text = line.strip().split("|")[2]
        id_to_text[id] = text


def get_data(wavs, id_to_text, maxlen=50):
    """ returns mapping of audio paths and transcription texts """
    data = []
    for w in wavs:
        id = w.split("/")[-1].split(".")[0]
        if len(id_to_text[id]) < maxlen:
            data.append({"audio": w, "text": id_to_text[id]})
    return data


## Preprocess the dataset

In [ ]:

class VectorizeChar:
    def __init__(self, max_len=50):
        self.vocab = (
            ["-", "#", "<", ">"]
            + [chr(i + 96) for i in range(1, 27)]
            + [" ", ".", ",", "?"]
        )
        self.max_len = max_len
        self.char_to_idx = {}
        for i, ch in enumerate(self.vocab):
            self.char_to_idx[ch] = i

    def __call__(self, text):
        text = text.lower()
        text = text[: self.max_len - 2]
        text = "<" + text + ">"
        pad_len = self.max_len - len(text)
        return [self.char_to_idx.get(ch, 1) for ch in text] + [0] * pad_len

    def get_vocabulary(self):
        return self.vocab


max_target_len = 200  # all transcripts in out data are < 200 characters
data = get_data(wavs, id_to_text, max_target_len)
vectorizer = VectorizeChar(max_target_len)
print("vocab size", len(vectorizer.get_vocabulary()))


def create_text_ds(data):
    texts = [_["text"] for _ in data]
    text_ds = [vectorizer(t) for t in texts]
    text_ds = tf.data.Dataset.from_tensor_slices(text_ds)
    return text_ds


def path_to_audio(path):
    # spectrogram using stft
    audio = tf.io.read_file(path)
    audio, _ = tf.audio.decode_wav(audio, 1)
    audio = tf.squeeze(audio, axis=-1)
    stfts = tf.signal.stft(audio, frame_length=200, frame_step=80, fft_length=256)
    x = tf.math.pow(tf.abs(stfts), 0.5)
    # normalisation
    means = tf.math.reduce_mean(x, 1, keepdims=True)
    stddevs = tf.math.reduce_std(x, 1, keepdims=True)
    x = (x - means) / stddevs
    audio_len = tf.shape(x)[0]
    # padding to 10 seconds
    pad_len = 2754
    paddings = tf.constant([[0, pad_len], [0, 0]])
    x = tf.pad(x, paddings, "CONSTANT")[:pad_len, :]
    return x


def create_audio_ds(data):
    flist = [_["audio"] for _ in data]
    audio_ds = tf.data.Dataset.from_tensor_slices(flist)
    audio_ds = audio_ds.map(
        path_to_audio, num_parallel_calls=tf.data.AUTOTUNE
    )
    return audio_ds


def create_tf_dataset(data, bs=4):
    audio_ds = create_audio_ds(data)
    text_ds = create_text_ds(data)
    ds = tf.data.Dataset.zip((audio_ds, text_ds))
    ds = ds.map(lambda x, y: {"source": x, "target": y})
    ds = ds.batch(bs)
    ds = ds.prefetch(tf.data.AUTOTUNE)
    return ds


split = int(len(data) * 0.99)
train_data = data[:split]
test_data = data[split:]
ds = create_tf_dataset(train_data, bs=64)
val_ds = create_tf_dataset(test_data, bs=4)

## Callbacks to display predictions

In [ ]:

class DisplayOutputs(keras.callbacks.Callback):
    def __init__(
        self, batch, idx_to_token, target_start_token_idx=27, target_end_token_idx=28
    ):
        """Displays a batch of outputs after every epoch

        Args:
            batch: A test batch containing the keys "source" and "target"
            idx_to_token: A List containing the vocabulary tokens corresponding to their indices
            target_start_token_idx: A start token index in the target vocabulary
            target_end_token_idx: An end token index in the target vocabulary
        """
        self.batch = batch
        self.target_start_token_idx = target_start_token_idx
        self.target_end_token_idx = target_end_token_idx
        self.idx_to_char = idx_to_token

    def on_epoch_end(self, epoch, logs=None):
        if epoch % 5 != 0:
            return
        source = self.batch["source"]
        target = self.batch["target"].numpy()
        bs = tf.shape(source)[0]
        preds = self.model.generate(source, self.target_start_token_idx)
        preds = preds.numpy()
        for i in range(bs):
            target_text = "".join([self.idx_to_char[_] for _ in target[i, :]])
            prediction = ""
            for idx in preds[i, :]:
                prediction += self.idx_to_char[idx]
                if idx == self.target_end_token_idx:
                    break
            print(f"target:     {target_text.replace('-','')}")
            print(f"prediction: {prediction}\n")


## Learning rate schedule

In [ ]:

class CustomSchedule(keras.optimizers.schedules.LearningRateSchedule):
    def __init__(
        self,
        init_lr=0.00001,
        lr_after_warmup=0.001,
        final_lr=0.00001,
        warmup_epochs=15,
        decay_epochs=85,
        steps_per_epoch=203,
    ):
        super().__init__()
        self.init_lr = init_lr
        self.lr_after_warmup = lr_after_warmup
        self.final_lr = final_lr
        self.warmup_epochs = warmup_epochs
        self.decay_epochs = decay_epochs
        self.steps_per_epoch = steps_per_epoch

    def calculate_lr(self, epoch):
        """ linear warm up - linear decay """
        warmup_lr = (
            self.init_lr
            + ((self.lr_after_warmup - self.init_lr) / (self.warmup_epochs - 1)) * epoch
        )
        decay_lr = tf.math.maximum(
            self.final_lr,
            self.lr_after_warmup
            - (epoch - self.warmup_epochs)
            * (self.lr_after_warmup - self.final_lr)
            / (self.decay_epochs),
        )
        return tf.math.minimum(warmup_lr, decay_lr)

    def __call__(self, step):
        epoch = step // self.steps_per_epoch
        return self.calculate_lr(epoch)


## Create & train the end-to-end model

In [ ]:
batch = next(iter(val_ds))

# The vocabulary to convert predicted indices into characters
idx_to_char = vectorizer.get_vocabulary()
display_cb = DisplayOutputs(
    batch, idx_to_char, target_start_token_idx=2, target_end_token_idx=3
)  # set the arguments as per vocabulary index for '<' and '>'

model = Transformer(
    num_hid=200,
    num_head=2,
    num_feed_forward=400,
    target_maxlen=max_target_len,
    num_layers_enc=4,
    num_layers_dec=1,
    num_classes=34,
)
loss_fn = tf.keras.losses.CategoricalCrossentropy(
    from_logits=True, label_smoothing=0.1,
)

learning_rate = CustomSchedule(
    init_lr=0.00001,
    lr_after_warmup=0.001,
    final_lr=0.00001,
    warmup_epochs=15,
    decay_epochs=85,
    steps_per_epoch=len(ds),
)
optimizer = keras.optimizers.Adam(learning_rate)
model.compile(optimizer=optimizer, loss=loss_fn)

history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb], epochs=1)

In practice, you should train for around 100 epochs or more.

Some of the predicted text at or around epoch 35 may look as follows:
```
target:     <as they sat in the car, frazier asked oswald where his lunch was>
prediction: <as they sat in the car frazier his lunch ware mis lunch was>

target:     <under the entry for may one, nineteen sixty,>
prediction: <under the introus for may monee, nin the sixty,>
```

# Test Open Russian Dataset

## Setup & Import

In [ ]:
import torchaudio
!git clone https://github.com/snakers4/open_stt
import numy as np
import pandas as pd

In [ ]:
import pandas as pd
def read_manifest(manifest_path):
    return pd.read_csv(manifest_path,
                       names=['wav_path','text_path','duration'])

## Load Russian Datasets(STT/ASR)
https://github.com/snakers4/open_stt

In [ ]:
import torchaudio
!git clone https://github.com/snakers4/open_stt

In [ ]:
import pandas as pd
def read_manifest(manifest_path):
    return pd.read_csv(manifest_path,
                       names=['wav_path','text_path','duration'])

All files are normalized for easier / faster runtime augmentations and processing as follows:
- Converted to mono, if necessary;
- Converted to 16 kHz sampling rate, if necessary;
- Stored as 16-bit integers;

## Config file & Batch downloading

In [ ]:
%%writefile  /content/md5sum_some.lst
dc6e33299e09d804eb6cedad49c7866a archives/buriy_audiobooks_2_val.tar.gz
2599f9a8c226418e201d82651288014b manifests/buriy_audiobooks_2_val.csv

Overwriting /content/md5sum_some.lst


In [ ]:
# # 34419c7d29cc21d8d1a280c78dd6aa5c archives/private_buriy_audiobooks_2.tar.gz
# # 243a13f8b6a8b98f3742abc85ae77bdb manifests/private_buriy_audiobooks_2.csv

## Direct downloading

In [ ]:
!wget https://azureopendatastorage.blob.core.windows.net/openstt/ru_open_stt_opus/archives/buriy_audiobooks_2_val.tar.gz
!wget https://azureopendatastorage.blob.core.windows.net/openstt/ru_open_stt_opus/manifests/buriy_audiobooks_2_val.csv


--2022-05-09 13:49:48--  https://azureopendatastorage.blob.core.windows.net/openstt/ru_open_stt_opus/archives/buriy_audiobooks_2_val.tar.gz
Resolving azureopendatastorage.blob.core.windows.net (azureopendatastorage.blob.core.windows.net)... 52.240.48.36
Connecting to azureopendatastorage.blob.core.windows.net (azureopendatastorage.blob.core.windows.net)|52.240.48.36|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 496479919 (473M) [application/octet-stream]
Saving to: ‘buriy_audiobooks_2_val.tar.gz.1’

buriy_audiobooks_2_ 100%[===================>] 473.48M   120MB/s    in 3.9s    

2022-05-09 13:49:52 (122 MB/s) - ‘buriy_audiobooks_2_val.tar.gz.1’ saved [496479919/496479919]

--2022-05-09 13:49:52--  https://azureopendatastorage.blob.core.windows.net/openstt/ru_open_stt_opus/archives/buriy_audiobooks_2_val.csv
Resolving azureopendatastorage.blob.core.windows.net (azureopendatastorage.blob.core.windows.net)... 52.240.48.36
Connecting to azureopendatastorage.blob

In [ ]:
!du -sh /content/*

728K	/content/buriy_audiobooks_2_val.csv
474M	/content/buriy_audiobooks_2_val.tar.gz
4.0K	/content/md5sum_some.lst
55M	/content/sample_data
95M	/content/speechbrain


In [ ]:
import os
for f_name in os.listdir('/content/'):
  if os.path.isfile(f_name):
    !du -h /content/$f_name

474M	/content/buriy_audiobooks_2_val.tar.gz
728K	/content/buriy_audiobooks_2_val.csv


## Read manifest (metadata)

In [ ]:
%cd /content/
#from utils.open_stt_utils import read_manifest
from open_stt.utils.open_stt_utils import read_manifest

manifest_df = read_manifest('buriy_audiobooks_2_val.csv')
manifest_df

/content


wav_path  \
0     buriy_audiobooks_2_val/0/60/3b9e3e73f32e.wav   
1     buriy_audiobooks_2_val/f/ee/4ad576fd66d8.wav   
2     buriy_audiobooks_2_val/a/41/fbd6f4e39de3.wav   
3     buriy_audiobooks_2_val/3/cd/b4244173d871.wav   
4     buriy_audiobooks_2_val/5/ff/d21714aa935f.wav   
...                                            ...   
7845  buriy_audiobooks_2_val/1/69/49f490ce2664.wav   
7846  buriy_audiobooks_2_val/2/81/4e1f6f81d814.wav   
7847  buriy_audiobooks_2_val/7/f4/5a8e31d324e3.wav   
7848  buriy_audiobooks_2_val/2/94/2b8c274cd853.wav   
7849  buriy_audiobooks_2_val/3/db/85798b286dcd.wav   

                                         text_path  duration  
0     buriy_audiobooks_2_val/0/60/3b9e3e73f32e.txt      0.32  
1     buriy_audiobooks_2_val/f/ee/4ad576fd66d8.txt      0.34  
2     buriy_audiobooks_2_val/a/41/fbd6f4e39de3.txt      0.34  
3     buriy_audiobooks_2_val/3/cd/b4244173d871.txt      0.34  
4     buriy_audiobooks_2_val/5/ff/d21714aa935f.txt      0.35  
...                                            ...       ...  
7845  buriy_audiobooks_2_val/1/69/49f490ce2664.txt     16.76  
7846  buriy_audiobooks_2_val/2/81/4e1f6f81d814.txt     17.27  
7847  buriy_audiobooks_2_val/7/f4/5a8e31d324e3.txt     17.97  
7848  buriy_audiobooks_2_val/2/94/2b8c274cd853.txt     18.35  
7849  buriy_audiobooks_2_val/3/db/85798b286dcd.txt     21.69  

[7850 rows x 3 columns]

In [ ]:
total_duration = manifest_df["duration"].sum()
print(f"total_duration: {total_duration}sec or {round(total_duration/3600)}h {round(total_duration%3600/60)}min {round(total_duration%3600%60)}sec")
print(f'min duration: {manifest_df["duration"].min()}sec, max duration: {manifest_df["duration"].max()}sec, mean duration: {round(manifest_df["duration"].mean())}sec')

total_duration: 17658.68sec or 5h 54min 19sec
min duration: 0.32sec, max duration: 21.69sec, mean duration: 2sec


## Unpack .tar.gz

In [ ]:
!tar -xf /content/buriy_audiobooks_2_val.tar.gz

## Lookup data

### Choose parts

In [ ]:
manifest_df["part"].nunique(), manifest_df["part"].unique()

(16, array(['0', 'f', 'a', '3', '5', 'c', 'd', 'e', '9', 'b', '8', '1', '4',
        '6', '7', '2'], dtype=object))

In [ ]:
manifest_df["part"] = manifest_df["wav_path"].apply(lambda x: x.split('/')[1])
manifest_df["subpart"] = manifest_df["wav_path"].apply(lambda x: x.split('/')[2])
# https://stackoverflow.com/questions/19798153/difference-between-map-applymap-and-apply-methods-in-pandas
# map is defined on Series ONLY
# applymap is defined on DataFrames ONLY
# apply is defined on BOTH
# https://sparkbyexamples.com/pandas/pandas-apply-function-usage-examples/
#manifest_df[["wav_path"]].applymap(lambda x: x.split('/')[1:3])
#manifest_df.filter(manifest_df['part']).head(2)
display(manifest_df.query('part == "0"').head(2),manifest_df.query('part == "0"').query('subpart == "60"'))

wav_path  \
0   buriy_audiobooks_2_val/0/60/3b9e3e73f32e.wav   
83  buriy_audiobooks_2_val/0/78/5188c9c31980.wav   

                                       text_path  duration part subpart  
0   buriy_audiobooks_2_val/0/60/3b9e3e73f32e.txt      0.32    0      60  
83  buriy_audiobooks_2_val/0/78/5188c9c31980.txt      0.45    0      78

wav_path  \
0     buriy_audiobooks_2_val/0/60/3b9e3e73f32e.wav   
2077  buriy_audiobooks_2_val/0/60/04bff9287970.wav   
2803  buriy_audiobooks_2_val/0/60/3394d6b3cf5c.wav   

                                         text_path  duration part subpart  
0     buriy_audiobooks_2_val/0/60/3b9e3e73f32e.txt      0.32    0      60  
2077  buriy_audiobooks_2_val/0/60/04bff9287970.txt      1.13    0      60  
2803  buriy_audiobooks_2_val/0/60/3394d6b3cf5c.txt      1.35    0      60

In [ ]:
def read_txt_from_file(f_name):
  with open(f_name,'r') as f:
    lines =f.readlines()
    return lines
import numpy as np
from IPython.display import display, Audio
len(manifest_df.query('part == "0"').values), manifest_df.query('part == "0"').values[:5]
p="0"
manifest_df_p = manifest_df.query(f'part == "{p}"')
len_p = len(manifest_df_p.values)
manifest_df_p.values[0]

array(['buriy_audiobooks_2_val/0/60/3b9e3e73f32e.wav',
       'buriy_audiobooks_2_val/0/60/3b9e3e73f32e.txt', 0.32, '0', '60'],
      dtype=object)

In [ ]:
cnt = 10
i_arr = np.random.randint(0,len_p, cnt  )
for i in i_arr:
  print(read_txt_from_file(manifest_df_p.values[i][1]))
  display(Audio(manifest_df_p.values[i][0]))

['записной книжки\n']


['нож рукоятка которого торчала перпендикулярно её рёбрам полностью вошёл\n']


['того чтобы получить ордер ему понадобится не меньше часа так что я ещё ничего не\n']


['был способен убить даже животное\n']


['своему мерседесу\n']


['и философия почесывая бока была\n']


['память приоткрывает завесу мрака\n']


['крышки\n']


['мы миновав бесконечно длинный мост выезжаем из сан франсиско\n']


['тех же платьях что были\n']


In [ ]:
from IPython.display import display, Audio
#from IPython import Audio
def read_txt_from_file(f_name):
  with open(f_name,'r') as f:
    lines =f.readlines()
    return lines
j=0
for i, row in enumerate(manifest_df.itertuples(index=False)):
    if row[2]>10:
      #print(row, '\n', row[0])
      print(row[2], read_txt_from_file(row[1]))
      display(Audio(row[0]))
      
      j+=1
    #else: i-=1
    if j>2: break

10.02 ['бок и вдавил спусковой крючок его пуля пролетела между атаманом и чеченей помощник упал ничком а макота придерживая шляпу бросился за\n']


10.02 ['стал твоим альфонсом мне страшно встречаться с прежними друзьями я стыжусь своей жизни своего лица своих рук володя кричал долго беснуясь\n']
10.05 ['ненаказуемых поступках не могут считаться основанием для возбуждения уголовного дела вот так\n']


In [ ]:
import torchaudio
sig, sr = torchaudio.load(row[0])
print(sig.shape, sr, f"{sig.shape[1]/sr}s" )

torch.Size([1, 160800]) 16000 10.05s


# LibriSpeech Russian
https://www.openslr.org/96/

https://www.openslr.org/resources/96/ruls_data.tar.gz

## Load & Unrar

In [ ]:
!wget https://www.openslr.org/resources/96/ruls_data.tar.gz

--2022-05-20 12:25:18--  https://www.openslr.org/resources/96/ruls_data.tar.gz
Resolving www.openslr.org (www.openslr.org)... 46.101.158.64
Connecting to www.openslr.org (www.openslr.org)|46.101.158.64|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: http://openslr.elda.org/resources/96/ruls_data.tar.gz [following]
--2022-05-20 12:25:18--  http://openslr.elda.org/resources/96/ruls_data.tar.gz
Resolving openslr.elda.org (openslr.elda.org)... 141.94.109.138, 2001:41d0:203:ad8a::
Connecting to openslr.elda.org (openslr.elda.org)|141.94.109.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 9129924586 (8.5G) [application/x-gzip]
Saving to: ‘ruls_data.tar.gz.1’

ruls_data.tar.gz.1  100%[===================>]   8.50G   108MB/s    in 90s     

2022-05-20 12:26:48 (96.5 MB/s) - ‘ruls_data.tar.gz.1’ saved [9129924586/9129924586]



### Unpack .tar.gz

In [ ]:
!tar -xf /content/ruls_data.tar.gz

### Lookup manifest

#### Detect encoding

In [ ]:
import json
json_path='/content/test/manifest.json'
#json_path='/content/train/manifest.json'
import codecs
import chardet
from chardet.universaldetector import UniversalDetector
detector = UniversalDetector()
for line in open(json_path, 'rb'):
    detector.feed(line)
    if detector.done: break
detector.close()
print(detector.result)
encoding = detector.result["encoding"]

{'encoding': 'utf-8', 'confidence': 0.99, 'language': ''}


### Transform json lines

In [ ]:
json_path_in = json_path
json_path_out = 'test_c.json'
def transform_json_file(json_path_in, json_path_out, data_type='train'):
    f_i = open(json_path_in, 'r')
    lines = f_i.readlines()
    len_lines = len(lines)
    print(len(lines))
    f_o = open(json_path_out, 'w')
    f_o.write('{\n')
    for i, line in enumerate(lines): #    test_json = json.load(f)
        dict_line= json.loads(line)
        #print(dict_line)
        key = "-".join(dict_line['audio_filepath'].replace('.wav','').split('/'))
        new_dict = {}
        #new_dict[key] = {}
        new_dict['wav'] = '{data_root}/' + data_type +'/'+ dict_line['audio_filepath']
        new_dict['duration'] = dict_line['duration']
        new_dict['text'] = dict_line['text']
        #if i<3: print(new_dict)
        #if i> 1350: print (i, key)
        if i <= len_lines-2:
            f_o.write(f'"{key}": ' + json.dumps(new_dict)+',\n')
        else:
            f_o.write(f'"{key}": ' + json.dumps(new_dict)+'\n')
        #if i>3: break
    f_o.write('}')
    f_i.close()
    f_o.close()
    
transform_json_file(json_path_in, json_path_out, data_type='test')    
!head -2 '$json_path_in'
print(5*'**')
!tail -2 '$json_path_in'
print(5*'**')
!head -2 '$json_path_out'
print(5*'**')
!tail -4 '$json_path_out'

1352
{"audio_filepath": "audio/2671/2145/poemi_01_pushkin_0000.wav", "duration": 11.35, "text": "для вас души моей царицы красавицы для вас одних времен минувших небылицы в часы досугов золотых под шепот старины болтливой рукою верной я писал", "text_no_preprocessing": "Для вас, души моей царицы, Красавицы, для вас одних Времен минувших небылицы, В часы досугов золотых, Под шепот старины болтливой, Рукою верной я писал", "score": -1.5}
{"audio_filepath": "audio/2671/2145/poemi_01_pushkin_0001.wav", "duration": 2.1, "text": "примите ж вы мой труд игривый", "text_no_preprocessing": "Примите ж вы мой труд игривый!", "score": -0.41}
**********
{"audio_filepath": "audio/5548/2145/poemi_36_pushkin_0043.wav", "duration": 3.56, "text": "гордись таков и ты поэт и для тебя условий нет", "text_no_preprocessing": "Гордись: таков и ты, поэт, И для тебя условий нет.", "score": -0.36}
{"audio_filepath": "audio/5548/2145/poemi_36_pushkin_0046.wav", "duration": 5.71, "text": "но ты не слышишь идешь куд

In [ ]:
#with codecs.open(json_path_out, 'r',encoding=encoding, errors="ignore") as f:
with codecs.open(json_path_out, 'r', encoding=encoding) as f:
    test_json = json.load(f)

In [ ]:
list(test_json.items())[:2]

[('audio-2671-2145-poemi_01_pushkin_0000',
  {'duration': 11.35,
   'text': 'для вас души моей царицы красавицы для вас одних времен минувших небылицы в часы досугов золотых под шепот старины болтливой рукою верной я писал',
   'wav': '{data_root}/test/audio/2671/2145/poemi_01_pushkin_0000.wav'}),
 ('audio-2671-2145-poemi_01_pushkin_0001',
  {'duration': 2.1,
   'text': 'примите ж вы мой труд игривый',
   'wav': '{data_root}/test/audio/2671/2145/poemi_01_pushkin_0001.wav'})]

In [ ]:
data = [json.loads(line) for line in open(json_path_in, 'r')]
data

### Lookup audio: voices, texts

In [ ]:
import glob
import os

#file_lst = glob.glob('/content/test/audio/**/**/*.wav', recursive=True )
p_lst = os.listdir('/content/test/audio')
for p in p_lst:# ['2671','2826', '4471']:
    print(p.upper())
    file_lst = glob.glob(f'/content/test/audio/{p}/**/*.wav', recursive=True )
    cnt = 3
    i_arr = np.random.randint(0,len(file_lst), cnt  )
    for i in i_arr:
      print(file_lst[i])
      key = "-".join(file_lst[i].replace('.wav','').split('/')[3:])
      print(test_json[key]['text'])
      #print(read_txt_from_file(manifest_df_p.values[i][1]))
      display(Audio(file_lst[i]))

4372
/content/test/audio/4372/2145/poemi_15_pushkin_0167.wav
два трупа перед ним лежали убийца страшен был лицом


/content/test/audio/4372/2145/poemi_15_pushkin_0149.wav
он с криком пробудясь во тьме ревниво руку простирает


/content/test/audio/4372/2145/poemi_15_pushkin_0024.wav
и с шумом высыпал народ шатры разобраны телеги готовы двинуться в поход


3056
/content/test/audio/3056/2145/poemi_05_pushkin_0094.wav
раскинув невод по волнам рыбак на весла наклоненный плывет к лесистым берегам к порогу хижины смиренной


/content/test/audio/3056/2145/poemi_05_pushkin_0034.wav
ходит он один средь храмин горделивых супругу милую зовет лишь эхо сводов молчаливых руслану голос подает


...

/content/test/audio/2671/2145/poemi_02_pushkin_0080.wav
лишь изредка с унылым свистом бунтует вихорь в поле чистом и на краю седых небес качает обнаженный лес


/content/test/audio/2671/2145/poemi_01_pushkin_0135.wav
минута сладкого свиданья и для меня блеснула ты


2826
/content/test/audio/2826/2145/poemi_09_pushkin_0037.wav
и наконец любви тоска в печальной речи излилася ах русский русский для чего не зная сердца твоего тебе навек я предалася


/content/test/audio/2826/2145/poemi_09_pushkin_0016.wav
его любовь тебе заменит моей души печальный хлад


/content/test/audio/2826/2145/poemi_08_pushkin_0023.wav
и долго пленник молодой лежал в забвении тяжелом


### Duration, SampleRate

In [ ]:
json_path_in = '/content/test/manifest.json'
json_path_out = 'test_c.json'
transform_json_file(json_path_in, json_path_out, data_type='test')
with codecs.open(json_path_out, 'r', encoding=encoding) as f:
    test_json = json.load(f)
f.close()
json_path_in = '/content/train/manifest.json'
json_path_out = 'train_c.json'
transform_json_file(json_path_in, json_path_out, data_type='train')
with codecs.open(json_path_out, 'r', encoding=encoding) as f:
    train_json = json.load(f)   
f.close()    

1352
54472


In [ ]:
pd_test = pd.DataFrame.from_dict(test_json, orient= 'index').reset_index()
display(pd_test.head(2))
d_sec = pd_test['duration'].sum()
print(f"{d_sec}sec or {round(d_sec//3600)}h {round(d_sec%3600//60)}mim {round(d_sec%3600%60)}sec )")

index  \
0  audio-2671-2145-poemi_01_pushkin_0000   
1  audio-2671-2145-poemi_01_pushkin_0001   

                                                 wav  duration  \
0  {data_root}/test/audio/2671/2145/poemi_01_push...     11.35   
1  {data_root}/test/audio/2671/2145/poemi_01_push...      2.10   

                                                text  
0  для вас души моей царицы красавицы для вас одн...  
1                      примите ж вы мой труд игривый

9526.380000000001sec or 2h 38mim 46sec )


In [ ]:
pd_train = pd.DataFrame.from_dict(train_json, orient= 'index').reset_index()
display(pd_train.head(2))
d_sec = pd_train['duration'].sum()
print(f"{d_sec}sec or {round(d_sec//3600)}h {round(d_sec%3600//60)}mim {round(d_sec%3600%60)}sec )")

index  \
0  audio-295-162-Leo-Tolstoy-Detstvo-RUSSIAN-01-K...   
1  audio-295-162-Leo-Tolstoy-Detstvo-RUSSIAN-01-K...   

                                                 wav  duration  \
0  {data_root}/train/audio/295/162/Leo-Tolstoy-De...      9.76   
1  {data_root}/train/audio/295/162/Leo-Tolstoy-De...     11.30   

                                                text  
0  он сделал это так неловко что задел образок мо...  
1  я высунул нос из под одеяла остановил рукою об...

334028.33sec or 92h 47mim 8sec )


In [ ]:
pd_train.wav.values[1000]

'{data_root}/train/audio/8086/9515/icemarch_01_gul_0056.wav'

In [ ]:
p_lst_test = os.listdir('/content/test/audio')
p_lst_train = os.listdir('/content/train/audio')
p_lst_train

['8169', '8086', '9014', '295', '13587']

In [ ]:
pd_test["part"] = pd_test["wav"].apply(lambda x: x.split('/')[3]) #.reset_index()
pd_train["part"] = pd_train["wav"].apply(lambda x: x.split('/')[3])#.reset_index()
display(pd_train.head(2), pd_test.head(2))
#display(pd_test.query('part == "0"').head(2),pd_test.query('part == "0"').query('subpart == "60"'))

index  \
0  audio-295-162-Leo-Tolstoy-Detstvo-RUSSIAN-01-K...   
1  audio-295-162-Leo-Tolstoy-Detstvo-RUSSIAN-01-K...   

                                                 wav  duration  \
0  {data_root}/train/audio/295/162/Leo-Tolstoy-De...      9.76   
1  {data_root}/train/audio/295/162/Leo-Tolstoy-De...     11.30   

                                                text part  
0  он сделал это так неловко что задел образок мо...  295  
1  я высунул нос из под одеяла остановил рукою об...  295

index  \
0  audio-2671-2145-poemi_01_pushkin_0000   
1  audio-2671-2145-poemi_01_pushkin_0001   

                                                 wav  duration  \
0  {data_root}/test/audio/2671/2145/poemi_01_push...     11.35   
1  {data_root}/test/audio/2671/2145/poemi_01_push...      2.10   

                                                text  part  
0  для вас души моей царицы красавицы для вас одн...  2671  
1                      примите ж вы мой труд игривый  2671

In [ ]:
for p in p_lst_test:
  d_sec = pd_test.query(f"part=='{p}'").duration.sum()
  d_HMS = f"{round(d_sec//3600)}h {round(d_sec%3600//60)}mim {round(d_sec%3600%60)}sec"
  print(p, round(d_sec,2), d_HMS)

4372 1076.95 0h 17mim 57sec
3056 1877.78 0h 31mim 18sec
5548 471.63 0h 7mim 52sec
4471 1355.52 0h 22mim 36sec
4091 844.92 0h 14mim 5sec
2671 2807.13 0h 46mim 47sec
2826 1092.45 0h 18mim 12sec


In [ ]:
for p in p_lst_train:
  d_sec = pd_train.query(f"part=='{p}'").duration.sum()
  d_HMS = f"{round(d_sec//3600)}h {round(d_sec%3600//60)}mim {round(d_sec%3600%60)}sec"
  print(f"ReaderID: {p}", round(d_sec,2), d_HMS)

ReaderID: 8169 148885.25 41h 21mim 25sec
ReaderID: 8086 138116.01 38h 21mim 56sec
ReaderID: 9014 14806.09 4h 6mim 46sec
ReaderID: 295 7948.97 2h 12mim 29sec
ReaderID: 13587 24272.01 6h 44mim 32sec


### wav durations

In [ ]:
print (f"test: max_duration: {pd_test['duration'].max()}, min_duration: {pd_test['duration'].min()}" )
max_duration = 10
print(max_duration)
print(pd_test.query(f"duration > {max_duration}").shape[0], '/', pd_test.shape[0]) #.count() 
max_duration = 15
print(max_duration)
print(pd_test.query(f"duration > {max_duration}").shape[0], '/', pd_test.shape[0])

test: max_duration: 19.88, min_duration: 1.85
10
244 / 1352
15
47 / 1352


In [ ]:
print (f"test: max_duration: {pd_train['duration'].max()}, min_duration: {pd_train['duration'].min()}" )
max_duration = 10
print(max_duration)
print(pd_train.query(f"duration > {max_duration}").shape[0], '/', pd_train.shape[0]) #.count() 
max_duration = 15
print(max_duration)
print(pd_train.query(f"duration > {max_duration}").shape[0], '/', pd_train.shape[0]) #.count() 


test: max_duration: 20.0, min_duration: 1.02
10
6984 / 54472
15
1465 / 54472


### Text Lengths

In [ ]:
pd_test['text_length'] = pd_test['text'].apply(lambda x:len(x))
print (f"test: max_lentgh_text: {pd_test['text_length'].max()}, min_lentgh_text: {pd_test['text_length'].min()}" )
max_length = 200
print(max_length)
print(pd_test.query(f"text_length > {max_length}").shape[0], '/', pd_test.shape[0]) #.count() 
max_length = 250
print(max_length)
print(pd_test.query(f"text_length > {max_length}").shape[0], '/', pd_test.shape[0])


test: max_lentgh_text: 272, min_lentgh_text: 25
200
16 / 1352
250
3 / 1352


In [ ]:
pd_train['text_length'] = pd_train['text'].apply(lambda x:len(x))
print (f"test: max_lentgh_text: {pd_train['text_length'].max()}, min_lentgh_text: {pd_train['text_length'].min()}" )
max_length = 200
print(max_length)
print( pd_train.query(f"text_length > {max_length}").shape[0] ,'/', pd_train.shape[0])
max_length = 250
print(max_length)
print( pd_train.query(f"text_length > {max_length}").shape[0] ,'/', pd_train.shape[0])


test: max_lentgh_text: 324, min_lentgh_text: 14
200
1058 / 54472
250
168 / 54472


### Sizes

In [ ]:
print("train")
for dir in os.listdir('/content/train/audio'):
  !du -sh /content/train/audio/'$dir'
print("test")
for dir in os.listdir('/content/test/audio'):
  !du -sh /content/test/audio/'$dir'  

train
4.5G	/content/train/audio/8169
4.2G	/content/train/audio/8086
457M	/content/train/audio/9014
246M	/content/train/audio/295
750M	/content/train/audio/13587
test
34M	/content/test/audio/4372
58M	/content/test/audio/3056
15M	/content/test/audio/5548
42M	/content/test/audio/4471
26M	/content/test/audio/4091
87M	/content/test/audio/2671
34M	/content/test/audio/2826


In [ ]:
"""
4.5G	/content/train/audio/8169
4.2G	/content/train/audio/8086
"""
d = ["train", "test", "dev"]
t = ['8169', '8086']
for p in [d[0]]:
  print(p)
  for b_id in t:
    print("==> ", b_id)
    for dir in os.listdir(f'/content/datasets/{p}/audio/{b_id}'):
      # /content/datasets/train/audio/8086
      !du -sh /content/datasets/'$p'/audio/'$b_id'/'$dir'  

train
==>  8169
429M	/content/datasets/train/audio/8169/10422
579M	/content/datasets/train/audio/8169/12256
1.2G	/content/datasets/train/audio/8169/14105
2.4G	/content/datasets/train/audio/8169/13240
==>  8086
335M	/content/datasets/train/audio/8086/9515
432M	/content/datasets/train/audio/8086/7531
818M	/content/datasets/train/audio/8086/11365
1.8G	/content/datasets/train/audio/8086/15088
647M	/content/datasets/train/audio/8086/7771
255M	/content/datasets/train/audio/8086/13744


In [ ]:
import torch
import torchaudio
 

In [ ]:
fn = ['/content/train/audio/8169/10422/veshniyevody_01_turgenev_0001.wav',
'/content/test/audio/2671/2145/poemi_01_pushkin_0000.wav',
]
for fname in fn:
  waveform, sample_rate = torchaudio.load(fname)
  print(sample_rate)



16000
16000


# Baseline + Ru Librispeech Automatic Speech Recognition with Transformer
By baseline from Keras https://keras.io/examples/audio/transformer_asr/



## Setup & Import

In [ ]:
import os
import random
from glob import glob
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
import json
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [ ]:
!pip install jiwer
from jiwer import wer
from jiwer import cer
from jiwer import wil

     |████████████████████████████████| 50 kB 2.2 MB/s 
  Created wheel for python-Levenshtein: filename=python_Levenshtein-0.12.2-cp37-cp37m-linux_x86_64.whl size=149873 sha256=3b1e93ea9c8c686e9b35b5ba917058d68c2ebd62fbc860b7a7bae1bcf7ba0b11
  Stored in directory: /root/.cache/pip/wheels/05/5f/ca/7c4367734892581bb5ff896f15027a932c551080b2abd3e00d
Successfully built python-Levenshtein


In [ ]:
!pip install huggingface_hub
from huggingface_hub import upload_file
from huggingface_hub import notebook_login
from huggingface_hub import hf_hub_url, cached_download

     |████████████████████████████████| 84 kB 2.4 MB/s 


## Define the Transformer Input Layer

When processing past target tokens for the decoder, we compute the sum of
position embeddings and token embeddings.

When processing audio features, we apply convolutional layers to downsample
them (via convolution stides) and process local relationships.

In [ ]:

class TokenEmbedding(layers.Layer):
    def __init__(self, num_vocab=1000, maxlen=100, num_hid=64):
        super().__init__()
        self.emb = tf.keras.layers.Embedding(num_vocab, num_hid)
        self.pos_emb = layers.Embedding(input_dim=maxlen, output_dim=num_hid)

    def call(self, x):
        maxlen = tf.shape(x)[-1]
        x = self.emb(x)
        positions = tf.range(start=0, limit=maxlen, delta=1)
        positions = self.pos_emb(positions)
        return x + positions


class SpeechFeatureEmbedding(layers.Layer):
    def __init__(self, num_hid=64, maxlen=100):
        super().__init__()
        self.conv1 = tf.keras.layers.Conv1D(
            num_hid, 11, strides=2, padding="same", activation="relu"
        )
        self.conv2 = tf.keras.layers.Conv1D(
            num_hid, 11, strides=2, padding="same", activation="relu"
        )
        self.conv3 = tf.keras.layers.Conv1D(
            num_hid, 11, strides=2, padding="same", activation="relu"
        )
        self.pos_emb = layers.Embedding(input_dim=maxlen, output_dim=num_hid)

    def call(self, x):
        x = self.conv1(x)
        x = self.conv2(x)
        return self.conv3(x)


## Transformer Encoder Layer

In [ ]:

class TransformerEncoder(layers.Layer):
    def __init__(self, embed_dim, num_heads, feed_forward_dim, rate=0.1):
        super().__init__()
        self.att = layers.MultiHeadAttention(num_heads=num_heads, key_dim=embed_dim)
        self.ffn = keras.Sequential(
            [
                layers.Dense(feed_forward_dim, activation="relu"),
                layers.Dense(embed_dim),
            ]
        )
        self.layernorm1 = layers.LayerNormalization(epsilon=1e-6)
        self.layernorm2 = layers.LayerNormalization(epsilon=1e-6)
        self.dropout1 = layers.Dropout(rate)
        self.dropout2 = layers.Dropout(rate)

    def call(self, inputs, training):
        attn_output = self.att(inputs, inputs)
        attn_output = self.dropout1(attn_output, training=training)
        out1 = self.layernorm1(inputs + attn_output)
        ffn_output = self.ffn(out1)
        ffn_output = self.dropout2(ffn_output, training=training)
        return self.layernorm2(out1 + ffn_output)


## Transformer Decoder Layer

In [ ]:

class TransformerDecoder(layers.Layer):
    def __init__(self, embed_dim, num_heads, feed_forward_dim, dropout_rate=0.1):
        super().__init__()
        self.layernorm1 = layers.LayerNormalization(epsilon=1e-6)
        self.layernorm2 = layers.LayerNormalization(epsilon=1e-6)
        self.layernorm3 = layers.LayerNormalization(epsilon=1e-6)
        self.self_att = layers.MultiHeadAttention(
            num_heads=num_heads, key_dim=embed_dim
        )
        self.enc_att = layers.MultiHeadAttention(num_heads=num_heads, key_dim=embed_dim)
        self.self_dropout = layers.Dropout(0.5)
        self.enc_dropout = layers.Dropout(0.1)
        self.ffn_dropout = layers.Dropout(0.1)
        self.ffn = keras.Sequential(
            [
                layers.Dense(feed_forward_dim, activation="relu"),
                layers.Dense(embed_dim),
            ]
        )

    def causal_attention_mask(self, batch_size, n_dest, n_src, dtype):
        """Masks the upper half of the dot product matrix in self attention.

        This prevents flow of information from future tokens to current token.
        1's in the lower triangle, counting from the lower right corner.
        """
        i = tf.range(n_dest)[:, None]
        j = tf.range(n_src)
        m = i >= j - n_src + n_dest
        mask = tf.cast(m, dtype)
        mask = tf.reshape(mask, [1, n_dest, n_src])
        mult = tf.concat(
            [tf.expand_dims(batch_size, -1), tf.constant([1, 1], dtype=tf.int32)], 0
        )
        return tf.tile(mask, mult)

    def call(self, enc_out, target):
        input_shape = tf.shape(target)
        batch_size = input_shape[0]
        seq_len = input_shape[1]
        causal_mask = self.causal_attention_mask(batch_size, seq_len, seq_len, tf.bool)
        target_att = self.self_att(target, target, attention_mask=causal_mask)
        target_norm = self.layernorm1(target + self.self_dropout(target_att))
        enc_out = self.enc_att(target_norm, enc_out)
        enc_out_norm = self.layernorm2(self.enc_dropout(enc_out) + target_norm)
        ffn_out = self.ffn(enc_out_norm)
        ffn_out_norm = self.layernorm3(enc_out_norm + self.ffn_dropout(ffn_out))
        return ffn_out_norm


## Complete the Transformer model

Our model takes audio spectrograms as inputs and predicts a sequence of characters.
During training, we give the decoder the target character sequence shifted to the left
as input. During inference, the decoder uses its own past predictions to predict the
next token.

In [ ]:

class Transformer(keras.Model):
    def __init__(
        self,
        num_hid=64,
        num_head=2,
        num_feed_forward=128,
        source_maxlen=100,
        target_maxlen=100,
        num_layers_enc=4,
        num_layers_dec=1,
        num_classes=10,
    ):
        super().__init__()
        self.loss_metric = keras.metrics.Mean(name="loss")
        self.num_layers_enc = num_layers_enc
        self.num_layers_dec = num_layers_dec
        self.target_maxlen = target_maxlen
        self.num_classes = num_classes

        self.enc_input = SpeechFeatureEmbedding(num_hid=num_hid, maxlen=source_maxlen)
        self.dec_input = TokenEmbedding(
            num_vocab=num_classes, maxlen=target_maxlen, num_hid=num_hid
        )

        self.encoder = keras.Sequential(
            [self.enc_input]
            + [
                TransformerEncoder(num_hid, num_head, num_feed_forward)
                for _ in range(num_layers_enc)
            ]
        )

        for i in range(num_layers_dec):
            setattr(
                self,
                f"dec_layer_{i}",
                TransformerDecoder(num_hid, num_head, num_feed_forward),
            )

        self.classifier = layers.Dense(num_classes)

    def decode(self, enc_out, target):
        y = self.dec_input(target)
        for i in range(self.num_layers_dec):
            y = getattr(self, f"dec_layer_{i}")(enc_out, y)
        return y

    def call(self, inputs):
        source = inputs[0]
        target = inputs[1]
        x = self.encoder(source)
        y = self.decode(x, target)
        return self.classifier(y)

    @property
    def metrics(self):
        return [self.loss_metric]

    def train_step(self, batch):
        """Processes one batch inside model.fit()."""
        source = batch["source"]
        target = batch["target"]
        dec_input = target[:, :-1]
        dec_target = target[:, 1:]
        with tf.GradientTape() as tape:
            preds = self([source, dec_input])
            one_hot = tf.one_hot(dec_target, depth=self.num_classes)
            mask = tf.math.logical_not(tf.math.equal(dec_target, 0))
            loss = self.compiled_loss(one_hot, preds, sample_weight=mask)
        trainable_vars = self.trainable_variables
        gradients = tape.gradient(loss, trainable_vars)
        self.optimizer.apply_gradients(zip(gradients, trainable_vars))
        self.loss_metric.update_state(loss)
        return {"loss": self.loss_metric.result()}

    def test_step(self, batch):
        source = batch["source"]
        target = batch["target"]
        dec_input = target[:, :-1]
        dec_target = target[:, 1:]
        preds = self([source, dec_input])
        one_hot = tf.one_hot(dec_target, depth=self.num_classes)
        mask = tf.math.logical_not(tf.math.equal(dec_target, 0))
        loss = self.compiled_loss(one_hot, preds, sample_weight=mask)
        self.loss_metric.update_state(loss)
        return {"loss": self.loss_metric.result()}

    def generate(self, source, target_start_token_idx):
        """Performs inference over one batch of inputs using greedy decoding."""
        bs = tf.shape(source)[0]
        enc = self.encoder(source)
        dec_input = tf.ones((bs, 1), dtype=tf.int32) * target_start_token_idx
        dec_logits = []
        for i in range(self.target_maxlen - 1):
            dec_out = self.decode(enc, dec_input)
            logits = self.classifier(dec_out)
            logits = tf.argmax(logits, axis=-1, output_type=tf.int32)
            last_logit = tf.expand_dims(logits[:, -1], axis=-1)
            dec_logits.append(last_logit)
            dec_input = tf.concat([dec_input, last_logit], axis=-1)
        return dec_input


## Download the dataset

Note: This requires ~3.6 GB of disk space and
takes ~5 minutes for the extraction of files.

### Functional

In [ ]:
%%time
%cd /content
if os.path.exists(os.path.join(os.getcwd(), "ruls_data.tar.gz")):
    print("Scipping downloading... file: ", "ruls_data.tar.gz", "is exists")
else:
    keras.utils.get_file(
        os.path.join(os.getcwd(), "ruls_data.tar.gz"),
        "https://www.openslr.org/resources/96/ruls_data.tar.gz",
        extract=True,
        archive_format="tar",
        cache_dir=".",
    )

# 2.4G	/content/datasets/train/audio/8169/13240
# 8169 - Reader_name tovarisch
# 13240/ALL	- Book_ID/CHAPTER_TITLE  Book Обрыв (Obryv) /ALL
# 
saveto = "./datasets/train/audio/8169/13240"
manifest_path = "./datasets/train/manifest.json"
wavs = glob(f"{saveto}/*.wav", recursive=True)

id_to_text = {}
with open(manifest_path, encoding="utf-8") as f:
    for line in f:
        dict_line = json.loads(line)
        key = "-".join(dict_line['audio_filepath'].replace('.wav','').split('/'))
        #new_dict['wav'] = '{data_root}/' + data_type +'/'+ dict_line['audio_filepath']
        #new_dict['duration'] = dict_line['duration']
        #new_dict['text'] = dict_line['text']

        id = key
        text = dict_line['text']
        id_to_text[id] = text

def get_data(wavs, id_to_text, maxlen=50):
    """ returns mapping of audio paths and transcription texts """
    data = []
    for w in wavs:
        #id = w.c[-1].split(".")[0]
        id = "-".join(w.split('/')[-4:]).split(".")[0]
        if len(id_to_text[id]) < maxlen:
            data.append({"audio": w, "text": id_to_text[id]})
    return data


/content
9129934848/9129924586 [==============================] - 339s 0us/step
CPU times: user 2min 45s, sys: 46.1 s, total: 3min 31s
Wall time: 8min 45s


### About Dataset

In [ ]:
!cat /content/datasets/README.TXT

GENERAL INFORMATION

Russian LibriSpeech (RuLS) dataset is based on LibriVox's public domain audio books (see BOOKS.TXT for the list of included books)
and contains about 98 hours of audio data.

The dataset was created by NVIDIA CORPORATION, 2020.
Contact info: ebakhturina@nvidia.com


The Russian LibriSpeech (RuLS) dataset is Public Domain in the USA. 


DIRECTORY STRUCTURE

.
├── BOOKS.TXT                                            # Info about the books included in the corpus
├── CHAPTERS_READERS.TXT                                 # Info readers and corresponding chapters/books
├── dev                                                  # DEV (validation) subset
│   └── audio
│       └── 5397                                         # LibriVox READER ID
│             ├── 2145                                   # LibriVox BOOK ID                         
│                   ├── poemi_12_pushkin_0000.wav        # Audio file in .wav format, 16 kHz
│                   ├── poemi_12_pushkin_

In [ ]:
!cat /content/datasets/BOOKS.TXT

;BOOK_ID: Book ID in the LibriVox project ID
;Title: Book title
;
;BOOK_ID| Title
13240	| Обрыв                                       | Obryv									| https://librivox.org/obryv-by-ivan-goncharov/
15088	| Силуэты русских писателей, Выпуск 3         | Silhouettes Russian Writers Issue 3)    | https://librivox.org/silhouettes-russian-writers-issue-3-by-yuly-aykhenvald/
14105	| Обыкновенная история 		        		  | Obyknovennaya Istorya					| https://librivox.org/obyknovennaya-istorya-by-ivan-goncharov/
11365	| Pассказы для детей и взрослых               | Short Stories for Children and Adults	| https://librivox.org/p-short-stories-for-children-and-adults-by-vsevolod-garshin/
7771	| Ранние рассказы                             | Early Short Stories						| https://librivox.org/early-short-stories-by-zeev-jabotinsky/
2145	| Поэмы                                       | Poems									| https://librivox.org/poemi-alexander-pushkin/ 
12256	| Дворянское гнездо                           | Dvoryan

In [ ]:
!cat /content/datasets/CHAPTERS_READERS.TXT

; BOOK_ID: Book ID in the LibriVox project ID
; CHAPTER_ID: The ID of the chapter on LibriVox
; CHAPTER_TITLE: The title of the chapter on LibriVox, 'ALL' - means the whole book is read by the same reader
; READER_ID: The ID of the reader in the LibriVox's database
; READER_NAME: The NAME of the reader in the LibriVox's database
; GENDER: Reader's gender
; SUBSET: The corpus subset to which this chapter is assigned
;
;BOOK_ID| CHAPTER_ID| CHAPTER_TITLE                                               | READER_ID| READER_NAME    | GENDER | SUBSET 
13240   | -         | ALL                                                         | 8169     | tovarisch      | M      | train  
15088   | -         | ALL                                                         | 8086     | Mark Chulsky   | M      | train  
14105   | -         | ALL                                                         | 8169     | tovarisch      | M      | train  
11365   | -         | ALL                                      

#### test functional download

In [ ]:
lines = f_i.readlines()
    len_lines = len(lines)
    print(len(lines))
    f_o = open(json_path_out, 'w')
    f_o.write('{\n')
    for i, line in enumerate(lines): #    test_json = json.load(f)
        dict_line= json.loads(line)
        #print(dict_line)
        key = "-".join(dict_line['audio_filepath'].replace('.wav','').split('/'))
        new_dict = {}
        #new_dict[key] = {}
        new_dict['wav'] = '{data_root}/' + data_type +'/'+ dict_line['audio_filepath']
        new_dict['duration'] = dict_line['duration']
        new_dict['text'] = dict_line['text']
        #if i<3: print(new_dict)
        #if i> 1350: print (i, key)
        if i <= len_lines-2:
            f_o.write(f'"{key}": ' + json.dumps(new_dict)+',\n')
        else:
            f_o.write(f'"{key}": ' + json.dumps(new_dict)+'\n')
        #if i>3: break
    f_o.write('}')

IndentationError: ignored

In [ ]:
# 2.4G	/content/datasets/train/audio/8169/13240
saveto = "./datasets/train/audio/8169/13240"
manifest_path = "./datasets/train/manifest.json"
wavs = glob(f"{saveto}/*.wav", recursive=True)

id_to_text = {}
with open(manifest_path, encoding="utf-8") as f:
    for line in f:
        dict_line = json.loads(line)
        key = "-".join(dict_line['audio_filepath'].replace('.wav','').split('/'))
        #new_dict['wav'] = '{data_root}/' + data_type +'/'+ dict_line['audio_filepath']
        #new_dict['duration'] = dict_line['duration']
        #new_dict['text'] = dict_line['text']

        id = key
        text = dict_line['text']
        id_to_text[id] = text

In [ ]:
wavs [:3], list(id_to_text)[:3]

In [ ]:
def get_data(wavs, id_to_text, maxlen=50):
    """ returns mapping of audio paths and transcription texts """
    data = []
    for w in wavs:
        #id = w.c[-1].split(".")[0]
        id = "-".join(w.split('/')[-4:]).split(".")[0]
        if len(id_to_text[id]) < maxlen:
            data.append({"audio": w, "text": id_to_text[id]})
    return data

In [ ]:
from IPython.display import Audio
data = get_data(wavs, id_to_text, maxlen=100)
i = np.random.randint(len(data))
print(i, len(data))
print(data[i]["text"])
display(Audio(data[i]["audio"]))


## Preprocess the dataset

In [ ]:
print([chr(i + ord('Я')) for i in range(1, 33)])

['а', 'б', 'в', 'г', 'д', 'е', 'ж', 'з', 'и', 'й', 'к', 'л', 'м', 'н', 'о', 'п', 'р', 'с', 'т', 'у', 'ф', 'х', 'ц', 'ч', 'ш', 'щ', 'ъ', 'ы', 'ь', 'э', 'ю', 'я']


In [ ]:

class VectorizeChar:
    def __init__(self, max_len=50):
        self.vocab = (
            ["-", "#", "<", ">"]
            #+ [chr(i + 96) for i in range(1, 27)]
            + [chr(i + ord('Я')) for i in range(1, 33)]
            + [" ", ".", ",", "?"]
        )
        self.max_len = max_len
        self.char_to_idx = {}
        for i, ch in enumerate(self.vocab):
            self.char_to_idx[ch] = i

    def __call__(self, text):
        text = text.lower()
        text = text[: self.max_len - 2]
        text = "<" + text + ">"
        pad_len = self.max_len - len(text)
        return [self.char_to_idx.get(ch, 1) for ch in text] + [0] * pad_len

    def get_vocabulary(self):
        return self.vocab


max_target_len = 200  # all transcripts in out data are < 200 characters
data = get_data(wavs, id_to_text, max_target_len)
vectorizer = VectorizeChar(max_target_len)
print("vocab size", len(vectorizer.get_vocabulary()))


def create_text_ds(data):
    texts = [_["text"] for _ in data]
    text_ds = [vectorizer(t) for t in texts]
    text_ds = tf.data.Dataset.from_tensor_slices(text_ds)
    return text_ds


def path_to_audio(path):
    # spectrogram using stft
    audio = tf.io.read_file(path)
    audio, _ = tf.audio.decode_wav(audio, 1)
    audio = tf.squeeze(audio, axis=-1)
    stfts = tf.signal.stft(audio, frame_length=200, frame_step=80, fft_length=256)
    x = tf.math.pow(tf.abs(stfts), 0.5)
    # normalisation
    means = tf.math.reduce_mean(x, 1, keepdims=True)
    stddevs = tf.math.reduce_std(x, 1, keepdims=True)
    x = (x - means) / stddevs
    audio_len = tf.shape(x)[0]
    # padding to 10 seconds
    pad_len = 2754
    paddings = tf.constant([[0, pad_len], [0, 0]])
    x = tf.pad(x, paddings, "CONSTANT")[:pad_len, :]
    return x


def create_audio_ds(data):
    flist = [_["audio"] for _ in data]
    audio_ds = tf.data.Dataset.from_tensor_slices(flist)
    audio_ds = audio_ds.map(
        path_to_audio, num_parallel_calls=tf.data.AUTOTUNE
    )
    return audio_ds


def create_tf_dataset(data, bs=4):
    audio_ds = create_audio_ds(data)
    text_ds = create_text_ds(data)
    ds = tf.data.Dataset.zip((audio_ds, text_ds))
    ds = ds.map(lambda x, y: {"source": x, "target": y})
    ds = ds.batch(bs)
    ds = ds.prefetch(tf.data.AUTOTUNE)
    return ds


split = int(len(data) * 0.99)
train_data = data[:split]
test_data = data[split:]
ds = create_tf_dataset(train_data, bs=64)
val_ds = create_tf_dataset(test_data, bs=4)

vocab size 40


In [ ]:
print(vectorizer.get_vocabulary())
vocab_size=len(vectorizer.get_vocabulary())

['-', '#', '<', '>', 'а', 'б', 'в', 'г', 'д', 'е', 'ж', 'з', 'и', 'й', 'к', 'л', 'м', 'н', 'о', 'п', 'р', 'с', 'т', 'у', 'ф', 'х', 'ц', 'ч', 'ш', 'щ', 'ъ', 'ы', 'ь', 'э', 'ю', 'я', ' ', '.', ',', '?']


## Callbacks to display predictions

In [ ]:
class DisplayOutputs(keras.callbacks.Callback):
    def __init__(
        #self, batch, idx_to_token, target_start_token_idx=27, target_end_token_idx=28
        self, batch, idx_to_token, target_start_token_idx=2, target_end_token_idx=3
    ):
        """Displays a batch of outputs after every epoch

        Args:
            batch: A test batch containing the keys "source" and "target"
            idx_to_token: A List containing the vocabulary tokens corresponding to their indices
            target_start_token_idx: A start token index in the target vocabulary
            target_end_token_idx: An end token index in the target vocabulary
        """
        self.batch = batch
        self.target_start_token_idx = target_start_token_idx
        self.target_end_token_idx = target_end_token_idx
        self.idx_to_char = idx_to_token

    def on_epoch_end(self, epoch, logs=None):
        if epoch % 5 != 0:
            return
        source = self.batch["source"]
        target = self.batch["target"].numpy()
        bs = tf.shape(source)[0]
        preds = self.model.generate(source, self.target_start_token_idx)
        preds = preds.numpy()
        print()
        for i in range(bs):
            target_text = "".join([self.idx_to_char[_] for _ in target[i, :]])
            prediction = ""
            for idx in preds[i, :]:
                prediction += self.idx_to_char[idx]
                if idx == self.target_end_token_idx:
                    break
            print(f"target:     {target_text.replace('-','')}")
            print(f"prediction: {prediction}")
            target_text_01 = target_text.replace('-','').replace('<','').replace('>','')
            prediction_01 = prediction.replace('<','').replace('>','')
            print(f"WER: {round(wer(target_text_01, prediction_01),4)*100:0.2f}%" ,
                  f"CER: {round(cer(target_text_01, prediction_01),4)*100:0.2f}%",
                  '\n')


## Checkpoint_callback

In [ ]:
checkpoint_filepath = './tmp/checkpoint'
model_ckpt_cb = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_filepath,
    save_weights_only=True,
    monitor='loss',
    mode='min',
    verbose=0,
    save_best_only=True)

## Learning rate schedule

In [ ]:

class CustomSchedule(keras.optimizers.schedules.LearningRateSchedule):
    def __init__(
        self,
        init_lr=0.00001,
        lr_after_warmup=0.001,
        final_lr=0.00001,
        warmup_epochs=15,
        decay_epochs=85,
        steps_per_epoch=203,
    ):
        super().__init__()
        self.init_lr = init_lr
        self.lr_after_warmup = lr_after_warmup
        self.final_lr = final_lr
        self.warmup_epochs = warmup_epochs
        self.decay_epochs = decay_epochs
        self.steps_per_epoch = steps_per_epoch

    def calculate_lr(self, epoch):
        """ linear warm up - linear decay """
        warmup_lr = (
            self.init_lr
            + ((self.lr_after_warmup - self.init_lr) / (self.warmup_epochs - 1)) * epoch
        )
        decay_lr = tf.math.maximum(
            self.final_lr,
            self.lr_after_warmup
            - (epoch - self.warmup_epochs)
            * (self.lr_after_warmup - self.final_lr)
            / (self.decay_epochs),
        )
        print("cuerrent LR", tf.math.minimum(warmup_lr, decay_lr))
        return tf.math.minimum(warmup_lr, decay_lr)

    def __call__(self, step):
        epoch = step // self.steps_per_epoch
        return self.calculate_lr(epoch)


## Create the end-to-end model

In [ ]:
batch = next(iter(val_ds))

# The vocabulary to convert predicted indices into characters
idx_to_char = vectorizer.get_vocabulary()
display_cb = DisplayOutputs(
    batch, idx_to_char, target_start_token_idx=2, target_end_token_idx=3
)  # set the arguments as per vocabulary index for '<' and '>'

model = Transformer(
    num_hid=200,
    num_head=2,
    num_feed_forward=400,
    target_maxlen=max_target_len,
    num_layers_enc=4,
    num_layers_dec=1,
    #num_classes=34,
    num_classes=len(vectorizer.get_vocabulary()) #40
)
loss_fn = tf.keras.losses.CategoricalCrossentropy(
    from_logits=True, label_smoothing=0.1,
)

learning_rate = CustomSchedule(
    init_lr=0.00001,
    lr_after_warmup=0.001,
    final_lr=0.00001,
    warmup_epochs=1, #7, #15,
    decay_epochs=3, #25, #85,
    steps_per_epoch=len(ds),
)

#backuop_restore_callback = tf.keras.callbacks.BackupAndRestore(backup_dir="./tmp/backup")

optimizer = keras.optimizers.Adam(learning_rate)
model.compile(optimizer=optimizer, loss=loss_fn)



## Save/Restore model

### Download model from HuggingFace

In [ ]:
from huggingface_hub import hf_hub_url, cached_download
from huggingface_hub import hf_hub_download

user_name="AndyGo"
repo_name= "keras-asr-transformer-ru-librispeech"
save_path = '/content/weights/'
file_name = 'model_weights.h5'
file_name = 'model_weights_2022_05_22_01.h5'

if not os.path.exists('/content/weights/'):
    !mkdir /content/weights/
else: 
    !rm '$save_path''$file_name'

#model.load_weights('/content/weights/model_weights.h5')
#file_name = 'model_weights.h5_05ep'

#config_file_url = hf_hub_url(f"{user_name}/{repo_name}", filename="config.json")
model_file_url= hf_hub_url(f"{user_name}/{repo_name}", filename=file_name, )
#cached_download(model_file_url) #,  cache_dir=save_path)
hf_hub_download(repo_id=f"{user_name}/{repo_name}", filename=file_name, force_filename=save_path+file_name)

Downloading:   0%|          | 0.00/20.6M [00:00<?, ?B/s]

'/content/weights/model_weights_2022_05_22_01.h5'

### Restore model

In [ ]:
## https://stackoverflow.com/questions/52826134/keras-model-subclassing-examples

## loading saved weights
"""
model = Transformer(
    num_hid=200,
    num_head=2,
    num_feed_forward=400,
    target_maxlen=max_target_len,
    num_layers_enc=4,
    num_layers_dec=1,
    #num_classes=34,
    num_classes=len(vectorizer.get_vocabulary()) #40
)
"""
file_name = 'model_weights_2022_05_22_01.h5'
model.build(([(None, None, 129),(None, 200)]))
"""
learning_rate = CustomSchedule(
    init_lr=0.00001,
    lr_after_warmup=0.001,
    final_lr=0.00001,
    warmup_epochs=3, # 3, #7 #15,
    decay_epochs=5, #25, #85,
    steps_per_epoch=len(ds),
)
"""
model.compile(optimizer=optimizer, loss=loss_fn)

model.load_weights('/content/weights/' + file_name)

### Save model

In [ ]:
# print (val_ds)
# 'source': TensorSpec(shape=(None, None, 129), dtype=tf.float32, name=None), 'target': TensorSpec(shape=(None, 200), dtype=tf.int32,  name=None)}>

<PrefetchDataset element_spec={'source': TensorSpec(shape=(None, None, 129), dtype=tf.float32, name=None), 'target': TensorSpec(shape=(None, 200), dtype=tf.int32, name=None)}>


In [ ]:
## https://stackoverflow.com/questions/52826134/keras-model-subclassing-examples
## saving weights
file_name = 'model_weights_2022_05_22_01.h5'
if not os.path.exists('/content/weights/'):
    !mkdir /content/weights/
"""
model = Transformer(
    num_hid=200,
    num_head=2,
    num_feed_forward=400,
    target_maxlen=max_target_len,
    num_layers_enc=4,
    num_layers_dec=1,
    #num_classes=34,
    num_classes=len(vectorizer.get_vocabulary()) #40
)
"""
#model.build(([(None, None, 129),(None, 200)]))
#model.summary()
model.save_weights('/content/weights/' + file_name)



### Save to HuggingFace

In [ ]:
!mkdir /content/HF
%cd /content/HF/
!git init
!git lfs install
notebook_login()

/usr/local/lib/python3.7/dist-packages/huggingface_hub/hf_api.py:587: FutureWarning: HfApi.login: This method is deprecated in favor of `set_access_token` and will be removed in v0.7.
  FutureWarning,


Login successful
Your token has been saved to /root/.huggingface/token
Authenticated through git-credential store but this isn't the helper defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub. Run the following command in your terminal in case you want to set this credential helper as the default

git config --global credential.helper store


In [ ]:
user_name="AndyGo"
repo_name= "keras-asr-transformer-ru-librispeech"
from_path = '/content/weights/'
file_name = 'model_weights.h5'
file_name = 'model_weights_2022_05_22_01.h5'
upload_file(
      path_or_fileobj=from_path + file_name,
      path_in_repo = file_name, 
      repo_id=user_name+'/'+ repo_name, 
      ) 

'https://huggingface.co/AndyGo/keras-asr-transformer-ru-librispeech/blob/main/model_weights_2022_05_22_01.h5'

In [ ]:
import pickle
with open('/content/weights/history_2022_05_22_p01.pickle', 'wb') as f:
    pickle.dump(history.history, f, protocol=pickle.HIGHEST_PROTOCOL)
#with open('/content/weights/history.pickle', 'rb') as f:
#    history = pickle.load(f)    

file_name_l = 'history_2022_05_22_p01.pickle'
upload_file(
      path_or_fileobj=from_path + file_name_l,
      path_in_repo = file_name_l, 
      repo_id=user_name+'/'+ repo_name, 
      ) 

'https://huggingface.co/AndyGo/keras-asr-transformer-ru-librispeech/blob/main/history_2022_05_22_p01.pickle'

In [ ]:
history.history.keys()

dict_keys(['loss', 'val_loss'])

## Train the model 20/05/2022

In practice, you should train for around 100 epochs or more.

Some of the predicted text at or around epoch 35 may look as follows:
```
target:     <as they sat in the car, frazier asked oswald where his lunch was>
prediction: <as they sat in the car frazier his lunch ware mis lunch was>

target:     <under the entry for may one, nineteen sixty,>
prediction: <under the introus for may monee, nin the sixty,>
```

In [ ]:
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb], epochs=2)

Epoch 1/2
178/178 [==============================] - ETA: 0s - loss: 1.4253target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <но о и не но но п о ст о м и не ти о неаеаа ное оеее но н о  о ова стос еса о осте и ино о ое и ова у  о но о ное са пол о н ва  не ос оне но д м олаа о на м ости нрае сто новстр  ност и и по нои и о

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <но о и не но но п о ст о м и не ти о неаеаа ное оеее но н о  о ова стос еса о осте и ино о ое и ова у  ола по ное са пол о н ва  не ос оне но д м олаа о на м ости нрае сто новстр  ност и и по нои и о

target:     <дай бог чтоб в ивана ивановича>
prediction: <но о и не но но п о ст о меао ти новв наеаа ное оеее но н о  о ова стос еса о осте и ино о ое и ова у  ола по ное са пол о н ва  не ос оне но д м олаа о на м ое но рае сто новстр  ност и и по нои и о

target:     <и эту то тиш

In [ ]:
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_checkpoint_callback], epochs=10)

Epoch 1/10
178/178 [==============================] - ETA: 0s - loss: 1.0583target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <он вото не прото ве вото не ве ве не пре сто пре сто по пре прето пре пре вотототото во претототототототото не на вототото тотото не ни не не пра тототе по то>

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <сказал вона сто сто сто сто во сто сто сто сторала сто сто сто сто сто>

target:     <дай бог чтоб в ивана ивановича>
prediction: <он во те не не то потото на пото на>

target:     <и эту то тишину этот след люди и назвали святой возвышенной любовью когда страсть сгорела и потухла>
prediction: <он сто поне сто поротото во во сто сто прала сто сто про сто вото про сто вото про ве прала во стото вотора стовостово вототовото сто не стото стотора сто>

178/178 [==============================] - 212s 1s/step - loss: 1.0583 

KeyboardInterrupt: ignored

In [ ]:
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_checkpoint_callback], epochs=7)

Epoch 1/7
178/178 [==============================] - ETA: 0s - loss: 0.9560target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <вот не коне вот како воне вот не водет не вот поте не воте се не воте не пете не подет нет пет сетет поте пете пот не нете воте не пот пете вотет оте не во пе не не не воте>

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <но пошл полчаско ол сане пошл самерил ос>

target:     <дай бог чтоб в ивана ивановича>
prediction: <да вечто вечто в ванеча в пом>

target:     <и эту то тишину этот след люди и назвали святой возвышенной любовью когда страсть сгорела и потухла>
prediction: <и тот сли вето сли вето потототь сли потото сли ве сли потототото пототототь пото верали сли потототь сли поть сли по сли сли сли сли потототототототототото>


Epoch 1: loss improved from inf to 0.95604, saving model to /tmp/checkpoint
178/178 [======

KeyboardInterrupt: ignored

In [ ]:
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_checkpoint_callback], epochs=7)

Epoch 1/7
178/178 [==============================] - ETA: 0s - loss: 0.7959target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <вот кого от макоговорит кого от коговорил оно казыват мая как отет кры от ко ней дет ко ко не не бе не бе не не не не не не не бе не бе не бе бе не бе не на бе не не бе во де>

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <но прошл полча пошло полча пошл полча пошло полчас>

target:     <дай бог чтоб в ивана ивановича>
prediction: <да и ван ванывича>

target:     <и эту то тишину этот след люди и назвали святой возвышенной любовью когда страсть сгорела и потухла>
prediction: <и потухла и потухли васть тотух как когда тух как как когда тоту тухла и потухлала и с в в вередеререредерето и ветототото и по веде свере касверетотететостетерере>


Epoch 1: loss improved from inf to 0.79595, saving model to ./tmp/checkpoint
178/178

KeyboardInterrupt: ignored

In [ ]:
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_checkpoint_callback, backuop_restore_callback], epochs=10)

Epoch 1/10
178/178 [==============================] - ETA: 0s - loss: 1.4438target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <о н ннее  а сто ла о т  не товоре е на  ни  т ото на л н на ик на  о  ли не з ни ни сснатя о ни ни ни наои е и то на ла ни ли не о  не  л а етоде нв  то  и а ла е на н ни  ото ое етя нв пр ои  на о о

WER: 254.17000000000002%
CER: 107.41000000000001%
target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <о н ннее  а сто ла о т  не товоре е на  ни  т отоооо л н на ик на  о  ли не з ни ни сснатя о ни ни ни наои нис то на ла ни ли не оо не  л а етоде нв  то  и а ла е на н ни  ото ое етя нв пр ои  на о о

WER: 762.5%
CER: 321.15%
target:     <дай бог чтоб в ивана ивановича>
prediction: <о н ннее  а сто ла о т  не товоре е на  ни  т отоооо л н на ик на  о  ли не з ни ни сснатя о ни ни ни наои нис то на лаов оли не оо не  л а етоде нв  

KeyboardInterrupt: ignored

## Train the model 21/05/2022

### **Train model**

#### p1 10 epochs

In [ ]:
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_checkpoint_callback], epochs=10)

Epoch 1/10
178/178 [==============================] - ETA: 0s - loss: 1.4094target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <о и в и неа на стеа да стоеа стери  о на ся в сте не ве в отл о ро на и с нс и по по сти и о не по в и с не по ро постте сте не о по ос стерил о ал нето и ва о рио ои пене и не п и оа о нрил  ио ил р
WER: 258.33% CER: 108.27%
target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <о и в и неа на стеа да стоеа стери  о на ся в сте не ве в отл о ро на и с нс и по по сти и о не по в и с не по ро постте сте не о по ос стерил о ал нето и ва о рио ои пене и не п и оа о нрил  ио ил р
WER: 800.0% CER: 338.0%
target:     <дай бог чтоб в ивана ивановича>
prediction: <о и в и неа на стеа и и стеа стери  о на ся в сте не ве в отл о ро на и с нс и по по сти и о не по в и с не по ро постте сте не о по ос стерил о ал нето и ва о рио ои пене и не 

#### p2 15 epochs

In [ ]:
%cd /content/
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_checkpoint_callback], epochs=15)

/content
Epoch 1/15
178/178 [==============================] - ETA: 0s - loss: 1.0718target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <он воде пола во сто вото во ве стора пра постово сто пра стово сто сто востостора валала во во сто на сто не ве пра валала пра во не по востоверала ве нера пра на на стова вастори стостосто>
WER: 162.5% CER: 106.77000000000001%
target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <он воде пола во сто вото во ве стора пра постово сто пра стово сто сто востостора валала во во сто на сто не ве пра валала пра во не по востоверала ве нера пра на на стова вастори стостосто>
WER: 487.5% CER: 310.0%
target:     <дай бог чтоб в ивана ивановича>
prediction: <он воде пола во сто вото во ве стора пра постово сто пра стово сто сто востостора валала во во сто на сто не ве пра валала пра во не по востоверала ве нера пра на на стова вас

#### p3 5 epochs

In [ ]:
%cd /content/
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_checkpoint_callback], epochs=5)
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_ckpt_cb], epochs=5)

/content
Epoch 1/5
178/178 [==============================] - ETA: 0s - loss: 1.3651
target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <она на на о на на на по на на о сто по в по во в на сте в о сто не по сто сто не ва сто не и по по на ва по на сто на ото не в не по о по не се ва на по о не ста на пова ве ве о ото в не о е по по во
WER: 266.67% CER: 110.53% 

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <она на на по в на на по во на о сто по в по во в на сте в о стото о по не сто не ва стоне и по ве но на на по сто по пото не в не по ов на не не да о по о не пра на пова ве ве по и ва по о е по по во
WER: 800.0% CER: 334.0% 

target:     <дай бог чтоб в ивана ивановича>
prediction: <она на на по ва на сто на сто о сто по во на по во по не ва стото о по не сто не ва стоне и по ве но на на по стото по но по в не по ов на нера ва на по о не пра на

### Plot History

## Train the model 21/05/2022 p2

### p1 25 epochs

In [ ]:
%cd /content/
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_ckpt_cb], epochs=25)

/content
Epoch 1/25
178/178 [==============================] - ETA: 0s - loss: 1.4355
target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <о о и но о оела н н о не о сдо се на лст у не о мо о ла у о о и оло о но о  на ес оо о на и о оо ои о ва ит на о оя не оо о о о о о  оне о но е вдо о о в  не е еда о ува ее оего ои  и не о е т сдегва
WER: 291.67% CER: 111.28% 

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <оне и но о оела н н о не о сдо се на лсттттта о мо о ла у о о и оло о но о  на ес оо о на и о оо ои о ва ит на о оя не оо о о о о о  оне о но е вдо о о в  не е еда о ува ее оего ои  и не о е т сдегва
WER: 850.0% CER: 336.0% 

target:     <дай бог чтоб в ивана ивановича>
prediction: <оне и но о оела н н о не о сдо се на лсттттта о мо о ла у о о и оло о но о  на ес оо о на и о оо ои о ва ит на о оя не оо о о о о о  оне о но е вдонй о в  не е еда

### p2 15 epochs

In [ ]:
%cd /content/
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_ckpt_cb], epochs=15)

/content
Epoch 1/15
178/178 [==============================] - ETA: 0s - loss: 0.3627
target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <вот моя одождемия одождемия одождемия одожденя казывая на бесетк и от моя одож сеткрыльцо говорильцо говорильцо говорил она бите>
WER: 87.5% CER: 68.42% 

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <но прошло полчас а занавес а занавес а занавесконене диврге весконе>
WER: 100.0% CER: 56.00000000000001% 

target:     <дай бог чтоб в ивана ивановича>
prediction: <дай бух чтоб вы вановича>
WER: 66.67% CER: 30.0% 

target:     <и эту то тишину этот след люди и назвали святой возвышенной любовью когда страсть сгорела и потухла>
prediction: <и назвале и потух когда слет згорела и потух когда свет звалет звалет то тух когда свет звалет свет звалет>
WER: 100.0% CER: 78.79% 

178/178 [==============================] - 

### p3 16 epochs

In [ ]:
%cd /content/
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_ckpt_cb], epochs=16)

/content
Epoch 1/16
178/178 [==============================] - ETA: 0s - loss: 0.3129
target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <вот мое одождеятся кам нее на дож сетку вот мои одож сетку вот моя одож сетку вот и пот моя одож сетку вот и пот и пот и пот и пот и пот и пот и пот и потаку>
WER: 145.82999999999998% CER: 81.95% 

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <но прошло полчас озановесконе одиргилась>
WER: 75.0% CER: 28.000000000000004% 

target:     <дай бог чтоб в ивана ивановича>
prediction: <дай бучтоб вы вановича>
WER: 83.33% CER: 33.33% 

target:     <и эту то тишину этот след люди и назвали святой возвышенной любовью когда страсть сгорела и потухла>
prediction: <и назвале и потух когда слетовью этот страсть звалет звалет звалет то слетовью этот страсть звалет ну люди этото слет>
WER: 105.88% CER: 75.76% 

178/178 [=======

## Train the model 22/05/2022 p1

### p1 36 epochs

In [ ]:
%cd /content/
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_ckpt_cb], epochs=36)

/content
Epoch 1/36
178/178 [==============================] - ETA: 0s - loss: 0.3172
target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <вот моя одож сетка мней указывая на дож сетку вот моя одож сетку вот моя одождетку вот и пот моя одождемите>
WER: 83.33% CER: 62.41% 

target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <но прошло полчас озановисконе одирю весконе одиргелось>
WER: 75.0% CER: 50.0% 

target:     <дай бог чтоб в ивана ивановича>
prediction: <дай бу чтоб вы вановича>
WER: 66.67% CER: 30.0% 

target:     <и эту то тишину этот след люди и назвали святой возвышенной любовью когда страсть сгорела и потухла>
prediction: <и назвали с горела и потух когда слетовью этот слетой свет згорела и потухи этот страсть звалет люди этотовью этото слет>
WER: 111.75999999999999% CER: 87.88% 

178/178 [==============================] - 224s 1s/step - loss: 

### p2 16 epochs warmup_epochs=0, lr_after_warmup = 0.0001

In [ ]:
model = Transformer(
    num_hid=200,
    num_head=2,
    num_feed_forward=400,
    target_maxlen=max_target_len,
    num_layers_enc=4,
    num_layers_dec=1,
    #num_classes=34,
    num_classes=len(vectorizer.get_vocabulary()) #40
)
model.build(([(None, None, 129),(None, 200)]))

learning_rate = CustomSchedule(
    init_lr=0.00001,  # 0.001, #
    lr_after_warmup=0.001, 
    final_lr=0.00001,
    warmup_epochs=1, #7, #15,
    decay_epochs=3, #25, #85,
    steps_per_epoch=len(ds),
)

optimizer = keras.optimizers.Adam(learning_rate)
file_name = 'model_weights_2022_05_22_01.h5'
model.load_weights('/content/weights/' + file_name)
model.compile(optimizer=optimizer, loss=loss_fn)



In [ ]:
import gc
gc.collect(); gc.collect(); gc.collect()

0

In [ ]:
%cd /content/
history = model.fit(ds, validation_data=val_ds, callbacks=[display_cb, model_ckpt_cb], epochs=16)

/content
Epoch 1/16


StagingError: ignored

## Inference

In [ ]:
target_start_token_idx = vectorizer.char_to_idx['<']
target_end_token_idx = vectorizer.char_to_idx['>']
vocab = vectorizer.get_vocabulary()
#print (vocab)
vectorizer_idx_to_char = {i: char for i, char in enumerate(vocab)}

### Fst predictions  - After 10 epochs

In [ ]:
#%%time
num_preds = 3
j=np.random.randint(len(data))
test_ds = create_tf_dataset(data[j:j+num_preds], bs=num_preds)

source = list(map(lambda x: x["source"], test_ds))[0] #[:num_preds]
target = list(map(lambda x: x["target"].numpy(), test_ds)) #[0] #[:num_preds]
bs = tf.shape(source)[0]
preds = model.generate(source, target_start_token_idx)
preds = preds.numpy()
#print()
for i in range(num_preds):
    #target_text = "".join([idx_to_char[_] for _ in target[i, :]])
    target_text = "".join([idx_to_char[_] for _ in target[0][i]])
    prediction = ""
    for idx in preds[i, :]:
        prediction += idx_to_char[idx]
        if idx == target_end_token_idx:
            break
    print(f"target:     {target_text.replace('-','')}")
    print(f"prediction: {prediction}")
    target_text_01 = target_text.replace('-','') #.replace('<','').replace('>','')
    prediction_01 = prediction #.replace('<','').replace('>','')
    print(f"WER: {round(wer(target_text_01, prediction_01),4)*100}%" ,
          f"CER: {round(cer(target_text_01, prediction_01),4)*100}%",
          '\n')

target:     <не откладывай же и порадуй бабушку приездом она тебе близка не по родству только а и по сердцу ты будучи молод это чувствовал не знаю каков стал в зрелых летах а был добрым внуком>
prediction: <в?жзм,#йыю#во#сьб?ыю#,инъьб,пб?рдайыч?ыюивв?ыиво?# ?#ввччжин#упщис>
WER: 100.0% CER: 88.94999999999999% 

target:     <как ни старалась она таиться но по временам проговаривалась каким нибудь нечаянно брошенным словом именем авторитета в той или другой сфере знания>
prediction: <в?жзм,#йыю#во#сьб?ыю#,инъо#э#ьб#у#ьбар?рнонъьмо#?# ?#ввччжин#упщис>
WER: 100.0% CER: 85.81% 

target:     <это был чистый светлый образ как перуджиниевская фигура простодушно и бессознательно живший и любивший с любовью пришедший в жизнь и с любовью отходящий от нее да с кроткой и тихой молитвой>
prediction: <в?жзм,#йыю#во#сьб?ыю#,инъо#э#ьб#у#ьбар?рнонъьмо#?# ?#ввччжин#упщис>
WER: 100.0% CER: 87.96000000000001% 



In [ ]:
source = next(iter(val_ds))["source"]
target = next(iter(val_ds))["target"].numpy()
bs = tf.shape(source)[0]

preds = model.generate(source, target_start_token_idx)
preds = preds.numpy()
for i in range(bs):
    target_text = "".join([vectorizer_idx_to_char[_] for _ in target[i, :]])
    prediction = ""
    for idx in preds[i, :]:
        prediction += vectorizer_idx_to_char[idx]
        if idx == target_end_token_idx:
            break
    print(f"target:     {target_text.replace('-','')}")
    print(f"prediction: {prediction}")
    target_text_01 = target_text.replace('-','').replace('<','').replace('>','')
    prediction_01 = prediction.replace('<','').replace('>','')
    print(f"WER: {round(wer(target_text_01, prediction_01),4)*100}%" ,
          f"CER: {round(cer(target_text_01, prediction_01),4)*100}%")


target:     <теперь я воспитываю пару бульдогов еще недели не прошло как они у меня а уж на огородах у нас ни одной кошки не осталось>
prediction: <оп,ижо,о,оом##?мфщя ожм?мтщящ,омжддщкшб,оькээ,оомож,яшжуьрша>
WER: 100.0% CER: 87.5%
target:     <но у него против воли обнаруживалось нетерпение ему вс# хотелось высказаться>
prediction: <оп,ижо,о,оом##?мфщя ожм?мтщящ,омжддожлкойу,ээ,оомож,яшжуьрша>
WER: 100.0% CER: 86.83999999999999%
target:     <к вечеру вера также разнемоглась у ней появился жар и бред>
prediction: <оп,ижо,о,оом##?мфщя ожм?мтщящ,омжддожлкойу,ээ,оомож,яшжуьрша>
WER: 100.0% CER: 96.55%
target:     <да с я так полагаю желал бы знать ваше мнение>
prediction: <оп,ижо,о,оом##?мфщожожм?мтщящ,омжддожлкойу,ээ,оомож,яшжуьрша>
WER: 100.0% CER: 126.66999999999999%


### Functional

In [ ]:
from IPython.display import Audio
def predict_transcribation(data_01, num_preds = None, max_preds=10):
    
    #test_ds = create_tf_dataset(data[j:j+num_preds], bs=num_preds)
    if isinstance(data_01, list):
        #print('list')
        #print(data_01)
        if num_preds is None:
            num_preds = min(max_preds, len(data_01))
        #test_ds = create_tf_dataset(data_01, bs=num_preds)
        
    elif isinstance(data_01, dict):
        num_preds = 1
        #print("dict")
        data_01 = [data_01]
        #test_ds = create_tf_dataset([data_01], bs=num_preds)
    else:
      print ('er')
      return
    test_ds = create_tf_dataset(data_01, bs=num_preds)  
    #test_ds = create_tf_dataset([data], bs=num_preds)
    source = list(map(lambda x: x["source"], test_ds))[0] #[:num_preds]
    target = list(map(lambda x: x["target"].numpy(), test_ds)) #[0] #[:num_preds]
    bs = tf.shape(source)[0]
    preds = model.generate(source, target_start_token_idx)
    preds = preds.numpy()
    #print()
    for i in range(num_preds):
        #target_text = "".join([idx_to_char[_] for _ in target[i, :]])
        target_text = "".join([idx_to_char[_] for _ in target[0][i]])
        prediction = ""
        for idx in preds[i, :]:
            prediction += idx_to_char[idx]
            if idx == target_end_token_idx:
                break
        display(Audio(data_01[i]['audio']))
        print(f"target:     {target_text.replace('-','')}")
        print(f"prediction: {prediction}")
        target_text_01 = target_text.replace('-','') #.replace('<','').replace('>','')
        prediction_01 = prediction #.replace('<','').replace('>','')
        print(f"WER: {round(wer(target_text_01, prediction_01),4)*100:0.2f}%" ,
              f"CER: {round(cer(target_text_01, prediction_01),4)*100:0.2f}%",
              '\n')

In [ ]:
#%%time
num_preds = 3
j=np.random.randint(len(data))
test_ds = create_tf_dataset(data[j:j+num_preds], bs=num_preds)

source = list(map(lambda x: x["source"], test_ds))[0] #[:num_preds]
target = list(map(lambda x: x["target"].numpy(), test_ds)) #[0] #[:num_preds]
bs = tf.shape(source)[0]
preds = model.generate(source, target_start_token_idx)
preds = preds.numpy()
#print()
for i in range(num_preds):
    #target_text = "".join([idx_to_char[_] for _ in target[i, :]])
    target_text = "".join([idx_to_char[_] for _ in target[0][i]])
    prediction = ""
    for idx in preds[i, :]:
        prediction += idx_to_char[idx]
        if idx == target_end_token_idx:
            break
    print(f"target:     {target_text.replace('-','')}")
    print(f"prediction: {prediction}")
    target_text_01 = target_text.replace('-','') #.replace('<','').replace('>','')
    prediction_01 = prediction #.replace('<','').replace('>','')
    print(f"WER: {round(wer(target_text_01, prediction_01),4)*100}%" ,
          f"CER: {round(cer(target_text_01, prediction_01),4)*100}%",
          '\n')

target:     <а вы на мой взгляд еще нездоровее сказал он>
prediction: <а вы на мой взгляд еще не здоровее сказал он>
WER: 22.220000000000002% CER: 2.22% 

target:     <что же вам угодно чтоб я сделал спросил он покорно>
prediction: <что же вам угодно чтоб я сделал спросил он покорно>
WER: 0.0% CER: 0.0% 

target:     <она подошла к обрыву шага на два робко заглянула туда и видела как с шумом раздавались кусты врозь и как райский точно по крупным уступам лестницы прыгал по горбам и впадинам оврага страсть какая>
prediction: <она подошла к обрыву шага на два робко заглянула туда и видела как рупным уступным уступомлесты в падглянулесь кусты вроси как райский точно покрая сто порагая ск сть сь к ск стым сь сты>
WER: 55.879999999999995% CER: 46.19% 



### Predictions

In [ ]:
target_start_token_idx = vectorizer.char_to_idx['<']
target_end_token_idx = vectorizer.char_to_idx['>']
vocab = vectorizer.get_vocabulary()
#print (vocab)
vectorizer_idx_to_char = {i: char for i, char in enumerate(vocab)}

#### 2022/05/22 01 - Train, Val Datasets

In [ ]:
j=np.random.randint(len(data))
predict_transcribation(data[j:j+2])
#predict_transcribation(data[j])

target:     <барыня требовала этого а машутке как то неловко было держать себя в чистоте>
prediction: <барыня требовала этого а машутке как то неловко было держать себя в чистоте>
WER: 0.0% CER: 0.0% 



target:     <он чаще прежнего заставал ее у часовни молящеюся>
prediction: <он чаще прежнего заставал ее у часовни молящеюся>
WER: 0.0% CER: 0.0% 



In [ ]:
j=np.random.randint(len(data))
print(j, len(data))
# train val split data by ratio: 90%/10%
#predict_transcribation(data[j:j+2])
predict_transcribation(data[j])

2752 11500


target:     <нет не голендуху а богатую и хорошенькую невесту>
prediction: <нет не голендуху а богатую и хорошенькую невесту>
WER: 0.00% CER: 0.00% 



In [ ]:
j=np.random.randint(len(data))
print(j, len(data))
# train val split data by ratio: 90%/10%
#predict_transcribation(data[j:j+2])
predict_transcribation(data[j])

5181 11500


target:     <пойдемте братец отсюда здесь пустотой пахнет сказала марфинька как ей не страшно одной я бы умерла>
prediction: <пойдемте братет сказала марфинька как ей не страшно одной я бы умерла>
WER: 31.25% CER: 29.00% 



#### 2022/05/22 01 - Eval Dataset

```
Need valuate data: look below
```

In [ ]:
j=np.random.randint(len(evaluate_data))
#predict_transcribation(evaluate_data[j:j+2])
predict_transcribation(evaluate_data[j])

target:     <он помялся на месте и нерешительно протянул руку вперед>
prediction: <он помялся на месте нерешь ик на месте нерешь ик нерешейк но месте нерешь ик но месте не ред>
WER: 166.67000000000002% CER: 91.23% 



In [ ]:
num_preds = 5
j_arr=np.random.randint(0, len(evaluate_data), num_preds)
data_for_predict = [ evaluate_data[j] for j in j_arr]
predict_transcribation(data_for_predict)


target:     <а панталеоне протягивает руку и указывает на санина кому>
prediction: <а под лего непродя гы ому и от луказывает люказывает насаниена>
WER: 100.0% CER: 60.34% 



target:     <позвольте мне ехать с вами пролепетал эмиль трепетным голосом и сложил руки>
prediction: <позольте ме лсожил руки пролипитал и мених а свай мили трепетал и мених а свайсложил руки>
WER: 116.67% CER: 58.440000000000005% 



target:     <старик совсем ослабел и запыхался>
prediction: <торик савсе мооался>
WER: 100.0% CER: 54.290000000000006% 



target:     <санин и она полюбили в первый раз>
prediction: <санен я она полюбили в пераз>
WER: 57.14% CER: 20.0% 



target:     <вы все деньги заплатили или только задаток дали>
prediction: <вы вседий ги за дотаги за дотаиль>
WER: 87.5% CER: 57.14% 



## Evaluate



### Prepare dataset for evaluate

```
# 429M	/content/datasets/train/audio/8169/10422 
# 8169 - Reader_name tovarisch
# 10422	- Book_ID/CHAPTER_TITLE   Вешние воды (Veshnie Vody) /All 
```

In [ ]:
saveto = "./datasets/train/audio/8169/10422"
manifest_path = "./datasets/train/manifest.json"
wavs_eval = glob(f"{saveto}/*.wav", recursive=True)

id_to_text_eval = {}
with open(manifest_path, encoding="utf-8") as f:
    for line in f:
        dict_line = json.loads(line)
        key = "-".join(dict_line['audio_filepath'].replace('.wav','').split('/'))
        id = key
        text = dict_line['text']
        id_to_text_eval[id] = text

max_target_len = 200  # all transcripts in out data are < 200 characters

evaluate_data = get_data(wavs_eval, id_to_text_eval, max_target_len)
#vectorizer = VectorizeChar(max_target_len)
split = int(len(evaluate_data) * 0.1)
evaluate_data_01 = evaluate_data[:split] # first 10%

split = int(len(evaluate_data) * 0.9)
evaluate_data_02 = evaluate_data[split:] # last 10%

eval_ds_01 = create_tf_dataset(evaluate_data_01, bs=4)
eval_ds_02 = create_tf_dataset(evaluate_data_02, bs=4)


In [ ]:
len(evaluate_data), len(evaluate_data_01), len(evaluate_data_02)

(2095, 209, 210)

### Functional

In [ ]:
def evaluate_asr(eval_ds, vectorizer= vectorizer):
    target_start_token_idx = vectorizer.char_to_idx['<']
    target_end_token_idx = vectorizer.char_to_idx['>']
    vocab = vectorizer.get_vocabulary()
    vectorizer_idx_to_char = {i: char for i, char in enumerate(vocab)}

    evals = []
    cnt = 0
    for k, batch in enumerate(eval_ds):
        source = batch["source"]
        target = batch["target"].numpy()
        bs = tf.shape(source)[0]
        preds = model.generate(source, target_start_token_idx)
        preds = preds.numpy()
        #print()
        for i in range(bs):
            target_text = "".join([idx_to_char[_] for _ in target[i, :]])
            prediction = ""
            for idx in preds[i, :]:
                prediction += vectorizer_idx_to_char[idx]
                if idx == target_end_token_idx:
                    break
            cnt +=1
            #print(cnt)
            target_text_01 = target_text.replace('-','').replace('<','').replace('>','')
            prediction_01 = prediction.replace('<','').replace('>','')
            wer_01 = round(wer(target_text_01, prediction_01),4)*100
            cer_01 = round(cer(target_text_01, prediction_01),4)*100
            evals.append([target_text_01, prediction_01, wer_01, cer_01])
            if k<2: 
                print(cnt)
                #print(cnt, ": ", end="")
                print(f"target:     {target_text.replace('-','')}")
                print(f"prediction: {prediction}")
                print(f"WER: {wer_01:0.2f}%" ,
                      f"CER: {cer_01:0.2f}%",
                      '\n')
    return evals

### Evaluation of Eval Dataset - first 10%

In [ ]:
%%time
evals_eval_01 = evaluate_asr(eval_ds_01)    

1
target:     <да ведь это прелесть проговорила она медлительным голосом это чудо>
prediction: <на витотет пренелий сприла она ми ди этот прелели счи улитет>
WER: 110.00% CER: 66.67% 

2
target:     <а что вот панталеоне мог бы в честь гостя тряхнуть стариной>
prediction: <а что в телихнусттлянуло бы вчись гость трянуло бы вчись гость трянулоние мое>
WER: 100.00% CER: 74.58% 

3
target:     <тут фрау леноре пришла в волнение и начала умолять свою дочь не сбивать с толку по крайней мере брата и удовольствоваться тем что она сама такая отчаянная республиканка>
prediction: <ту вришло в ришло в ришло в вришло в ришло в ришло в ришло в ришло в ришло в ришло в ришло в вришло в ришло в вришло в ришло в тв ропатаиемири брата>
WER: 117.86% CER: 75.00% 

4
target:     <но вот оно опять как будто тускнеет оно удаляется опускается на дно и лежит оно там чуть чуть шевеля плесом>
prediction: <но отна опять как будту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту ту 

In [ ]:
evals_eval_01_pd = pd.DataFrame(evals_eval_01,columns = ["target", "prediction", "wer", "cer"])

print("mean WER%:", round(np.mean(evals_eval_01_pd["wer"].values),2),
      "median WER%:", round(np.median(evals_eval_01_pd["wer"].values),2),
      "mean СER%:", round(np.mean(evals_eval_01_pd["cer"].values),2),
      "median CER%:", round(np.median(evals_eval_01_pd["cer"].values),2),
      
      )
display(evals_eval_01_pd.head(), evals_eval_01_pd.tail())  

mean WER%: 115.63 median WER%: 104.55 mean СER%: 74.12 median CER%: 71.88


target  \
0  да ведь это прелесть проговорила она медлитель...   
1  а что вот панталеоне мог бы в честь гостя трях...   
2  тут фрау леноре пришла в волнение и начала умо...   
3  но вот оно опять как будто тускнеет оно удаляе...   
4  казалось только теперь она вздохнула свободно ...   

                                          prediction     wer    cer  
0  на витотет пренелий сприла она ми ди этот прел...  110.00  66.67  
1  а что в телихнусттлянуло бы вчись гость трянул...  100.00  74.58  
2  ту вришло в ришло в ришло в вришло в ришло в р...  117.86  75.00  
3  но отна опять как будту ту ту ту ту ту ту ту т...  210.00  91.59  
4  казалос вободно и дугна и дугна и удуше ее тур...   78.57  60.00

target  \
204                    приступим ответил подпоручик но   
205    я сама не ожидала этого тихо проговорила джемма   
206  у ней мигрень прошла но она находилась в настр...   
207                      джемма не тотчас отвечала ему   
208                       с восхищением повторил санин   

                                            prediction    wer     cer  
204                                      бристу динооб  100.0   70.97  
205  я же дала и прогуворила дала этово тихо прогув...  125.0   65.96  
206  у ней мегими грепрошла нона находилась но ходи...  120.0   82.09  
207  мне точес ответил этила емон не  точипс ответи...  160.0  127.59  
208                      в исчением бовтолил санен дон  125.0   46.43

In [ ]:
evals_eval_01_pd.to_csv('evaluation_eval_ds_first10proc.csv', index=False)

### Evaluation of Eval Dataset - last 10%

In [ ]:
evals_eval_02 = evaluate_asr(eval_ds_02)    

1
target:     <господа туристы разъезжали в дилижансах>
prediction: <гсподатуристы звиещелие б дележамцих>
WER: 100.00% CER: 41.03% 

2
target:     <не прикажете ли сударыня я вам отыщу вашу карету>
prediction: <не прикажители вашу коря бам оты с на на маты сичу>
WER: 111.11% CER: 52.08% 

3
target:     <и говорят прибавил санин с особым ударением на слово говорят что твоя жена очень богата говорят и это>
prediction: <и гуворят и эта и эта куговорят что ванен собумудореньем слоговорят что ванен собумудорением собумудорят>
WER: 88.89% CER: 67.33% 

4
target:     <он явственно чувствовал и даже слышал как оно толкалось в ребра>
prediction: <нея встава идаже слышь какон у каконо токолось вен чуствова идаже слышл каконо токолась в регро>
WER: 136.36% CER: 80.95% 

5
target:     <сам он ни богат ни знатен ни умен>
prediction: <самом ни з на ни бага как не з ни бабрга не з на не бага>
WER: 175.00% CER: 100.00% 

6
target:     <я никогда не устаю отвечала она>
prediction: <я никагда никагда н

In [ ]:
evals_eval_02_pd = pd.DataFrame(evals_eval_02,columns = ["target", "prediction", "wer", "cer"])

print("mean WER%:", round(np.mean(evals_eval_02_pd["wer"].values),2),
      "median WER%:", round(np.median(evals_eval_02_pd["wer"].values),2),
      "mean СER%:", round(np.mean(evals_eval_02_pd["cer"].values),2),
      "median CER%:", round(np.median(evals_eval_02_pd["cer"].values),2),
      )
display(evals_eval_02_pd.head(), evals_eval_02_pd.tail())  

mean WER%: 115.43 median WER%: 100.0 mean СER%: 74.87 median CER%: 71.08


target  \
0            господа туристы разъезжали в дилижансах   
1   не прикажете ли сударыня я вам отыщу вашу карету   
2  и говорят прибавил санин с особым ударением на...   
3  он явственно чувствовал и даже слышал как оно ...   
4                  сам он ни богат ни знатен ни умен   

                                          prediction     wer     cer  
0               гсподатуристы звиещелие б дележамцих  100.00   41.03  
1  не прикажители вашу коря бам оты с на на маты ...  111.11   52.08  
2  и гуворят и эта и эта куговорят что ванен собу...   88.89   67.33  
3  нея встава идаже слышь какон у каконо токолось...  136.36   80.95  
4  самом ни з на ни бага как не з ни бабрга не з ...  175.00  100.00

target  \
205  пока ты меня не прогонишь отвечал он с отчаяни...   
206  он сошлется на самые несомненные свидетельства...   
207                         правда вы говорят женитесь   
208  сам он давным давно всю свою латынь забыл и об...   
209  даже имена пушкин она выговаривала пуссекин и ...   

                                            prediction     wer    cer  
205  как и мене пробкам своей глюбилалк рукам с вое...  100.00  76.74  
206  он с воочлеты нас самой неные свиделесть возсс...  137.50  72.58  
207                         правдо вы говорят женететь   50.00  11.54  
208  самон довным добным довным довным довным довны...   92.86  64.38  
209  даже и мена в глинька и глинька секен ичем тор...  130.77  77.92

In [ ]:
evals_eval_02_pd.to_csv('evaluation_eval_ds_last10proc.csv', index=False)

### Evaluation of Val Dataset - form main data (last 10%)

In [ ]:
print(len(test_data))

115


In [ ]:
%%time
evals_val = evaluate_asr(val_ds)  

1
target:     <вот моя академия говорил он указывая на беседку вот и портик это крыльцо а дождь идет в кабинете наберется ко мне юности облепят меня>
prediction: <вот моя ко бесед ли такрыльцо говорил он указывая на дож с кубеседку вот и пот и пот и пот и пот и пот и пот и пот и пот и пот и пот и пот и пот и пот и пот>
WER: 141.67% CER: 65.41% 

2
target:     <но прошло полчаса час а занавеска не отдергивалась>
prediction: <но прошло полчо полчаса озановилась часа озановис озановис озановилась>
WER: 75.00% CER: 72.00% 

3
target:     <дай бог чтоб в ивана ивановича>
prediction: <дай бучтоб выван иван ивановича>
WER: 66.67% CER: 26.67% 

4
target:     <и эту то тишину этот след люди и назвали святой возвышенной любовью когда страсть сгорела и потухла>
prediction: <и этот с горела и потухи этот с горела и потухи этот с горела и потухи этот с горела и потухин люди ина звале и потухина зывали светой вас ветой в згорела>
WER: 164.71% CER: 110.10% 

5
target:     <вера умна но он опытнее ее 

In [ ]:
evals_val_pd = pd.DataFrame(evals_val,columns = ["target", "prediction", "wer", "cer"])

print("mean WER%:", round(np.mean(evals_val_pd["wer"].values),2),
      "median WER%:", round(np.median(evals_val_pd["wer"].values),2),
      "mean СER%:", round(np.mean(evals_val_pd["cer"].values),2),
      "median CER%:", round(np.median(evals_val_pd["cer"].values),2),
      )
display(evals_val_pd.head(), evals_val_pd.tail())  

mean WER%: 94.2 median WER%: 90.48 mean СER%: 58.32 median CER%: 60.78


target  \
0  вот моя академия говорил он указывая на беседк...   
1  но прошло полчаса час а занавеска не отдергива...   
2                     дай бог чтоб в ивана ивановича   
3  и эту то тишину этот след люди и назвали свято...   
4           вера умна но он опытнее ее и знает жизнь   

                                          prediction     wer     cer  
0  вот моя ко бесед ли такрыльцо говорил он указы...  141.67   65.41  
1  но прошло полчо полчаса озановилась часа озано...   75.00   72.00  
2                    дай бучтоб выван иван ивановича   66.67   26.67  
3  и этот с горела и потухи этот с горела и потух...  164.71  110.10  
4   вера у но най жизнь у но опоть него и знай жизнь   88.89   52.50

target  \
110                   что же она рукодельем занимается   
111        потом лицо ее приняло равнодушное выражение   
112  нет не я татьяна марковна они велели мне уйти ...   
113                  а вы мне отчего не хотите угодить   
114  райский остановился остановил аянова ядовито у...   

                                            prediction     wer    cer  
110                     что же она рукодели мзаниается   40.00  12.50  
111   потом лица ее приняла равнодушног лица ее принял  100.00  32.56  
112  нет а оснами побежде меня побежде меня побежде...   90.48  70.30  
113          а вы меня тчего не хотите угодите угодить   42.86  33.33  
114  окое становился какое становился какое станови...  120.00  81.75

In [ ]:
evals_val_pd.to_csv('evaluation_val_ds.csv', index=False)

### Evaluate part of train data

In [ ]:
train_ds_eval = create_tf_dataset(train_data[:int(len(train_data)/40)], bs=4)

In [ ]:
print(len(train_data),int(len(train_data)/40))

11385 284


In [ ]:
%%time
evals_train_ds_eval = evaluate_asr(train_ds_eval)  

1
target:     <ужели он не поймет этого никогда и не воротится ни сюда к этой вечной правде>
prediction: <ужели он не поймет этого никогда и не воротится ни сюда к этой вечной правде>
WER: 0.00% CER: 0.00% 

2
target:     <думаю что шутите вы добрая не то что он поглядел на мать>
prediction: <думаю что шутите вы добрая не то что он поглядел на мать>
WER: 0.00% CER: 0.00% 

3
target:     <не раскайтесь после если я приму>
prediction: <не раскайтесь после если я приму>
WER: 0.00% CER: 0.00% 

4
target:     <но ведь вс# дело в воспитании зачем наматывать им старые понятия воспитывать по птичьи>
prediction: <но ведь вс# дело в воспитании зачем наматывать им старые понятия воспитывать по птичьи>
WER: 0.00% CER: 0.00% 

5
target:     <я с марфинькой хочу поехать на сенокос сегодня сказала бабушка райскому твоя милость хозяин не удостоишь ли взглянуть на свои луга>
prediction: <я с марфинькой хочу поехать на сенокос сегодня сказала бабушка райскому твоя милость хозяин не удостоишь ли взглянут

In [ ]:
evals_train_ds_eval_pd = pd.DataFrame(evals_train_ds_eval,columns = ["target", "prediction", "wer", "cer"])
print("mean WER%:", round(np.mean(evals_train_ds_eval_pd["wer"].values),2),
      "median WER%:", round(np.median(evals_train_ds_eval_pd["wer"].values),2),
      "mean СER%:", round(np.mean(evals_train_ds_eval_pd["cer"].values),2),
      "median CER%:", round(np.median(evals_train_ds_eval_pd["cer"].values),2),
      )
display(evals_train_ds_eval_pd.head(), evals_train_ds_eval_pd.tail())  

evals_train_ds_eval_pd.to_csv('evaluation_part_train_ds.csv', index=False)


mean WER%: 5.44 median WER%: 0.0 mean СER%: 4.29 median CER%: 0.0


target  \
0  ужели он не поймет этого никогда и не воротитс...   
1  думаю что шутите вы добрая не то что он погляд...   
2                   не раскайтесь после если я приму   
3  но ведь вс# дело в воспитании зачем наматывать...   
4  я с марфинькой хочу поехать на сенокос сегодня...   

                                          prediction  wer  cer  
0  ужели он не поймет этого никогда и не воротитс...  0.0  0.0  
1  думаю что шутите вы добрая не то что он погляд...  0.0  0.0  
2                   не раскайтесь после если я приму  0.0  0.0  
3  но ведь вс# дело в воспитании зачем наматывать...  0.0  0.0  
4  я с марфинькой хочу поехать на сенокос сегодня...  0.0  0.0

target  \
279              это только больше опечалило марфиньку   
280  хотя он поздно лег но встал рано чтобы передат...   
281     нарушил ли присягу в верности царю и отечеству   
282        очнувшись сказала она где я брала книги тут   
283  она обманула ее доверие и не устояла в своей г...   

                                            prediction  wer  cer  
279              это только больше опечалило марфиньку  0.0  0.0  
280  хотя он поздно лег но встал рано чтобы передат...  0.0  0.0  
281     нарушил ли присягу в верности царю и отечеству  0.0  0.0  
282        очнувшись сказала она где я брала книги тут  0.0  0.0  
283  она обманула ее доверие и не устояла в своей г...  0.0  0.0